In [3]:
import hashlib
import hmac
import csv
import numpy as np
import pandas as pd
import joblib
from joblib import Parallel, delayed
from multiprocessing import  Pool
import multiprocessing
import itertools
import random

In [4]:
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import average_precision_score, precision_recall_curve
from scipy import stats

In [5]:
from operator import itemgetter
import logging, sys

In [6]:
import warnings
warnings.filterwarnings("ignore")

In [7]:
_DEBUG = False
KAGGLE = False

In [8]:
# logging.basicConfig( #stream=sys.stdout, 
#                     level=logging.DEBUG)

In [9]:
# logging.debug('A debug message!')

In [10]:
pd.options.display.max_rows=2000
pd.options.display.max_columns=500
pd.set_option('display.max_colwidth', None)

In [11]:
import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

In [12]:
def calculate_roll(server_seed,client_seed,nonce):
    # Compute the HMAC-SHA512 hash of string1 using string2 as the key
    
    string1 = f"{nonce}:{server_seed}:{nonce}"
    hmac_key =   f"{nonce}:{client_seed}:{nonce}".encode()
    hmac_hash = hmac.new(key=hmac_key,
                         msg=string1.encode(),
                         digestmod=hashlib.sha512).hexdigest()

    # Convert the first 8 characters of the HMAC-SHA512 hash to an integer
    string3 = hmac_hash[:8]
    number = int(string3, 16)

    # Compute the roll value
    roll = round(number / 429496.7295)
    
    return roll

In [13]:
# Define a function to generate a single hash in the hash chain
def generate_hash(message):
    # Hash the message using SHA-256
    hash_obj = hashlib.sha256(message)

    # Get the hexadecimal representation of the hash
    hash_hex = hash_obj.hexdigest()

    # Return the hash
    return hash_hex

In [14]:
def generate_hash_chain(seed,chain_length):
    hash_list=[seed]
    message = seed.encode()
    for i in range(chain_length):
        hash_hex= generate_hash(message)
        # Write the hash to the CSV file
        hash_list.append(hash_hex)
        # Update the message with the current hash
        message = hash_hex.encode()
    return hash_list

def compute_multirolls(hash_list,client_seed,nonce):
    rolls=[]
    for cur_hash in hash_list:
        roll = calculate_roll(cur_hash,client_seed,nonce)
        rolls.append(roll)
    return rolls
def compute_multirolls_nonce(server_hash,client_seed,hash_list_nonce):
    rolls=[]
    for cur_hash_nonce in hash_list_nonce:
        roll = calculate_roll(server_hash,client_seed,cur_hash_nonce)
        rolls.append(roll)
    return rolls
def compute_multirolls_client(server_hash,client_seed_list,nonce):
    rolls=[]
    for cur_client in client_seed_list:
        roll = calculate_roll(cur_hash,client_seed,nonce)
        rolls.append(roll)
    return rolls

##### Machine Learning

In [15]:
hashval = 'b51436f61c47d15d4465705df24266c4790dcd255f0245b09c0b5fb8770740cb' #'3e24f29a3ae70e54aedd86b0c68640050be7dace8ae679f1fb85d1325a56ddae'
seed = hashval #'c77b3e783f094e255b0693f89094bed95ad9738d86f44fa4c09c8b0d58e2c73e'
nonce = 2705 #2390

# feature_chain_length=60
# train_hash_size = 2158#121
# train_client_size = 2000 
# test_client_size = 10000

In [16]:
PATTERN_99=False
HIGH_ANALYSIS=False

cur_digit = 9
cur_zero_digit = 0

In [17]:
OLD_VERSION_READ=False
READ_FROM_FILE=True

In [18]:
if PATTERN_99:
    file_pattern_str = 'x99x'
else:
    file_pattern_str = 'x00x'

In [19]:
HIGH_TARGET= 9000 #8944
LOW_TARGET = 1000 #1056
ZERO_COL_CUTOFF = 4

In [20]:
def create_target_mask(data,bHighCheck=HIGH_ANALYSIS):
    if bHighCheck:
        mask = data['roll_actual'] > HIGH_TARGET
    else:
        mask = data['roll_actual'] < LOW_TARGET   
    return mask

Prediction

#### Machine Learning

In [21]:
import xgboost as xgb
import matplotlib.pyplot as plt # for plotting graphs
import seaborn as sns # for plotting graphs
from sklearn.preprocessing import LabelEncoder
from imblearn.over_sampling import RandomOverSampler
from sklearn.metrics import accuracy_score, roc_auc_score, roc_curve, f1_score,precision_recall_curve

Train Validation Split

In [22]:
#This function is useful to convert the predicted probabilities into labels 
#so that F1 score is optimized
#It first determines the probability threshold using precision recall curve at which F1 score is optimized and 
#then generate the optimized labels based on the determined probability threshold
def get_opt_cutoff_prec(labels,preds):
    precision, recall, thresholds  = precision_recall_curve(labels, preds)
    f1_score= 2*((precision*recall)/(precision+recall))
    
    f1_score = f1_score[:len(thresholds)]
    f1_score[np.isnan(f1_score)]=0
#     optimal_idx = np.nanargmax(precision[:len(precision)-1])
#     print(f'precision borders:{precision[0],precision[len(precision)-2]}')
#     print(f'recall borders:{recall[0],recall[len(recall)-2]}')
#     print(f'f1_score size:{len(f1_score)} recall size:{len(recall)}')
#     print(f'{precision=}')
#     print(f'{recall=}')
#     print(f'{f1_score=}')
#     print(f'{thresholds=}')
#     print(f'optimal_idx:{optimal_idx} precision size:{len(precision)} thresholds size:{len(thresholds)}')
    optimal_idx = np.nanargmax(f1_score)
    optimal_threshold = thresholds[optimal_idx]
#     return optimal_threshold, precision[optimal_idx]
    return optimal_threshold, f1_score[optimal_idx]

def convert_probtolabels(preds,cutoff=0.5):
    y_bin= preds.copy()
    y_bin[preds>cutoff] = 1
    y_bin[preds<=cutoff] = 0
    y_bin=y_bin.astype(int)

    return y_bin

In [23]:
def generate_probs(multi_models,model,data,features):
    if multi_models:
        probs= np.zeros(len(data))
        for i,model_ind in enumerate(model):
            cur_prob= model_ind.predict_proba(data[features])[:,1] 
            probs+= cur_prob / len(model)
    else: 
        probs= model.predict_proba(test_filt_df[features_test])[:,1]
    data['probs']=probs
    return data

##### Prediction of Test 

In [24]:
CONT_ANALYSIS=False
IS_PROD=False

In [25]:
# if not IS_PROD:
    
#     actual_seed="075065a937673e7a74d4b4a06eaa125f9e195f42643a4ddf00e80032150b8793"
# #     actual_seed = cur_hash_list[25]
#     # Vectorize the function
#     vectorized_calculate_roll = np.vectorize(calculate_roll)

#     # Compute the roll values for the input arrays
#     roll_array = vectorized_calculate_roll(actual_seed,
#                                            results_df_test['client_seed'],
#                                            nonce)

#     results_df_test['roll_actual']=roll_array
# #     test_manual = generate_test_features(results_df_test)
#     test = generate_features_full(results_df_test,False,feature_chain_length)

In [26]:
def get_sim_summary(test_filt_all_k,
                       test_hash_cutoff_df,
                       is_imp_feats,imp_feats_count,
                       is_rank_pct=False):

    if is_imp_feats:
#         print('imp_feats_count:',imp_feats_count)
        hash_groups =[ [col for col in imp_df['feature'].values if (col.startswith('roll_'))][:imp_feats_count] ]
    else:
        hash_groups = [list(range(1,11)),list(range(25,36)),list(range(50,60)),list(range(100,111)) ]
    hash_groups_flat = [item for sublist in hash_groups for item in sublist]
#     print(hash_groups)
    
    
    if HIGH_ANALYSIS:
        success = (test_filt_all_k[hash_groups_flat] > HIGH_TARGET).sum(axis=1)
    else:
        success = (test_filt_all_k[hash_groups_flat] < LOW_TARGET).sum(axis=1)
    
    ratio_mean = success / len(hash_groups_flat)
    roll_mean = test_filt_all_k[hash_groups_flat].mean(axis=1)
    
#     sim_summary = pd.DataFrame()
    test_filt_all_k['k']=test_filt_all_k['k']
    test_filt_all_k['ratio_mean']=ratio_mean
    test_filt_all_k['roll_mean']=roll_mean
    
    test_filt_all_k['ratio_mean_rank']= test_filt_all_k['ratio_mean'].rank(method='min',
                                                                           ascending=True,pct=is_rank_pct)
    test_filt_all_k['roll_mean_rank']= test_filt_all_k['roll_mean'].rank(method='min',
                                                                         pct=is_rank_pct,
                                                                           ascending=True)
    test_filt_all_k['ratio_group_roll_rank']= test_filt_all_k.groupby('ratio_mean')['roll_mean'].rank(method='min',
                                                                                                     pct=is_rank_pct)   
    test_filt_all_k['ratio_group_roll_rank_desc']= test_filt_all_k.groupby('ratio_mean')['roll_mean'].rank(method='min',
                                                                                                          ascending=False,
                                                                                                          pct=is_rank_pct)   
    test_filt_all_k['probs_rank']= test_filt_all_k['probs'].rank(method='min',pct=is_rank_pct,
                                                                ascending=False)
    test_filt_all_k['ratio_group_probs_rank']= test_filt_all_k.groupby('ratio_mean')['probs'].rank(method='min',
                                                                                                   pct=is_rank_pct,
                                                                                                  ascending=False)   
#     for col in hash_groups_flat:
#         test_filt_all_k[f'{col}_rank']=test_filt_all_k[col].rank(method='min',
#                                                                 ascending=True,
#                                                                 pct=is_rank_pct)
    #     test_filt_all_k=sim_summary.reset_index(drop=True)
    
    return test_filt_all_k
    

In [27]:
# k_objs = [test_all_k_imp,test_all_k,df,features_test,all_k,top_k_ele,all_k_imp,top_k_ele_imp,imp_df]
# joblib.dump(k_objs,f'data/analysis/k_data_{nonce}_{file_pattern_str}_pattern.dump')

Machine Learning Model for match pos data generation

In [28]:
nonce = 2687

In [29]:
k_obj_all_nonces = []
#2688
nonce_list = [2673,2674,2675,2680,2681,2687,2688,2689,2690,2712] + list(range(2701,2711))
for cur_nonce in nonce_list:
    k_objs = joblib.load(f'data/analysis/k_data_{cur_nonce}_{file_pattern_str}_pattern.dump')
    k_obj_all_nonces.append(k_objs)
    print(cur_nonce)
    test_all_k_imp,test_all_k,df,features_test,all_k,top_k_ele,all_k_imp,top_k_ele_imp,imp_df = k_objs

2673
2674
2675
2680
2681
2687
2688
2689
2690
2712
2701
2702
2703
2704
2705
2706
2707
2708
2709
2710


In [30]:
test_all_k.head()

roll_actual  \
3533          825   
7398         5780   
1436         1136   
184          8615   
2221         4071   

                                                                  seed  \
3533  347945e51a2c44687d416916545cb27187dc5b85f76e07003ef7ebbc66d9d710   
7398  347945e51a2c44687d416916545cb27187dc5b85f76e07003ef7ebbc66d9d710   
1436  347945e51a2c44687d416916545cb27187dc5b85f76e07003ef7ebbc66d9d710   
184   347945e51a2c44687d416916545cb27187dc5b85f76e07003ef7ebbc66d9d710   
2221  347945e51a2c44687d416916545cb27187dc5b85f76e07003ef7ebbc66d9d710   

                                                                  hash  \
3533  dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
7398  dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
1436  dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
184   dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
2221  dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   

                                                                               client_seed  \
3533  woxpwoxpwoxpwoxpwoxp314ad1533464c3bd8fe7d7624f672a151b39c31aeab74dbb96de8ab7657bd523   
7398  woxpwoxpwoxpwoxpwoxp287b5f43718c9bc5c8003d5ba13b8792505328577d31c88d0712db643c037258   
1436  woxpwoxpwoxpwoxpwoxpa937e6169ef142a8ef1e5ea41b06f428d322d340cb82a833af3fd16f0619345e   
184   woxpwoxpwoxpwoxpwoxp2375370942362b5e9f4db7e56515ca4cc1ed2a372847238c6b9fbe3fed8f3ae5   
2221  woxpwoxpwoxpwoxpwoxp4b6cfa324871841274b3c55f1a3359294b1ce64bd6a68a04da57b60101b6b569   

      client_index  roll_0  roll_1  roll_2  roll_3  roll_4  roll_5  roll_6  \
3533        561633    7001    5508    3366    5741    8512    3248    2036   
7398         83919    1005     749    1863    2112    5440    1779    5289   
1436        825777    7005    8420    7979    2028    1393    8738    7120   
184         975524    8008    9344      56    5237    5253    5457    1578   
2221        724383    6006    9696    3613    7076    4144    4823    2559   

      roll_7  roll_8  roll_9  roll_10  roll_11  roll_12  roll_13  roll_14  \
3533    2290    9252    2573     7416     7811     9488     3513     5556   
7398    1929    4466    8517     4687     9816     5622     4426     1032   
1436    5370    9237    6624      912     6163     9401     7534      352   
184     9908    8676    3829     1347      309      271     8808     7230   
2221     786    6318    3533     2445     2616      922     7156     2508   

      roll_15  roll_16  roll_17  roll_18  roll_19  roll_20  roll_21  roll_22  \
3533     7425     3043     1678      868     6746     5417     6673     8388   
7398     3750     7340     2610     7552     5608     6605     2111     7792   
1436     7289     4014     2222     3473     8266     3822     2763     4456   
184       244     7372      360     3708     6344     6081     1854     6618   
2221     3900     2871     3953     2074     1430     2451     2233     5786   

      roll_23  roll_24  roll_25  roll_26  roll_27  roll_28  roll_29  roll_30  \
3533     5593     3448     3349     4810     8583     7525     4584     4327   
7398     3731     9593     1369     6845     6650      895     3097     4059   
1436     9550     2720     5399     3593     8137     5145     3650     2826   
184       709     7848     6076     8843     7066     6445     9226     9928   
2221     7415     4445     3380     8967      417     3072     7232     4087   

      roll_31  roll_32  roll_33  roll_34  roll_35  roll_36  roll_37  roll_38  \
3533     7850     7491     8146     7934     6723      745     4374     5182   
7398     4029     4344     2567     3876     1552     8010     4742     4256   
1436     2908     1186     3813     8009     7117     3921     3683     2408   
184      2320     6281     7058     4448     8187     8673     3878     6269   
2221     4697      230     2977     5348      643     9690     8359     6836   

      roll_39  roll_40  roll_41  roll_42  roll_43

In [27]:
a = np.array([9, 4, 4, 3, 3, 9, 0, 4, 6, 0])
print(a)

ind = np.argpartition(a, -5)[-5:]
# ind = np.argpartition(a, -5)[:5]
print(ind)

top4 = a[ind]
print(top4)

sorted_val  = np.argsort(a[ind])
print(sorted_val)
sorted_ind  = ind[sorted_val]
sorted_ind

a[sorted_ind]

[9 4 4 3 3 9 0 4 6 0]
[2 1 5 8 0]
[4 4 9 6 9]
[0 1 3 2 4]


array([4, 4, 6, 9, 9])

In [28]:
ind = np.argpartition(arr, -n)[-n:]

NameError: name 'arr' is not defined

In [102]:
def get_nlargest_ind(arr,n=10,asc=False):
    if not asc:
        ind = np.argpartition(arr, -n)[-n:]
    else:
        ind = np.argpartition(arr, -n)[:n]
    
    #     print(ind)

    topn= arr[ind]
#     print(topn)

    sorted_val=  np.argsort(arr[ind])
    if not asc:
        sorted_val=sorted_val[::-1]
#     print(sorted_val)
    sorted_ind  = ind[sorted_val]
    
    return sorted_ind



def get_top_success_count(probs,y,top_n=10,asc=False):
    
    top_prob_ind = get_nlargest_ind(probs,n=top_n,asc=asc)
    top_y = y[top_prob_ind]
    
#     print(f'{top_prob_ind=}')
#     print(f'{top_y=}')
#     print(f'{probs[top_prob_ind]}')
    
    total = top_n
    match_pos_arr = np.nonzero(top_y==1)[0]+1
    success = len(top_y[top_y==1])
    ratio = success / total
    
#     print(f'total:{total} success:{success} ratio:{ratio}')
    
    return success, ratio,top_prob_ind,match_pos_arr

def get_top_auc_score(probs,y,top_n=10,asc=False):
    
    top_prob_ind = get_nlargest_ind(probs,n=top_n,asc=asc)
    top_y = y[top_prob_ind]
    top_probs = probs[top_prob_ind]
    
    score = roc_auc_score(top_y, top_probs)
    
    return score

def cust_top_n_matches(y_pred, dtrain):
    y_true = dtrain.get_label()
    top_preds = 100
    success, ratio,top_prob_ind,match_pos_arr=get_top_success_count(y_pred,
                                                                    y_true,
                                                                  top_n=top_preds,asc=False)
    match_count = len(match_pos_arr)
    error = top_preds - match_count

    return 'top_n_matches', error

def cust_top_n_auc(y_pred, dtrain):
    y_true = dtrain.get_label()
    top_preds = 100
    auc_score=get_top_auc_score(y_pred,y_true,top_n=top_preds,asc=False)
    error = 1 - auc_score
    return 'top_n_matches', error

def gen_top_mean_data_ml(test_combined_imp,features_test,
                        n_estimators =100,asc=False,top_n=10,
                        random_over_sampler=False,use_best_iteration=False,
                        n_splits=5):
    params = { 'n_estimators':n_estimators,
              'max_leaves':25,
                'subsample':0.8,
              'random_state':145,
              # 'scale_pos_weight': 5,
    #           'max_depth':6,
            'learning_rate':0.05,
             'colsample_bytree':0.6,#0.85,
             'lambda':0.05,
             'alpha':0.1}

    # xgb_model = xgb.XGBClassifier(**params)
    xgb_models = []
    scores  = []
    ratios =[]
    tr_cutoffs=[]
    val_cutoffs=[]
    tr_last_cutoffs=[]
    val_cutoff_percs=[]
    
    X = test_combined_imp[features_test].reset_index(drop=True)
    y = test_combined_imp['target'].reset_index(drop=True)
    
    top_ratios = []
    iterations = []
    first_match_positions= []
    best_iterations =[]
    
    
    kfold = StratifiedKFold(n_splits=n_splits, random_state=756, shuffle=True)
    oof_probs = np.zeros(len(test_combined_imp))
    oversample = RandomOverSampler(sampling_strategy='minority',random_state=756)

    for fold,(tr_index, val_index) in enumerate(kfold.split(X, y)):
        X_tr,y_tr = X.iloc[tr_index],y.iloc[tr_index]
        X_val,y_val = X.iloc[val_index],y.iloc[val_index]
        
#         print(f'{val_index=}')

        # fit and apply the transform
        if random_over_sampler:
            X_tr, y_tr = oversample.fit_resample(X_tr, y_tr)
#         print(pd.Series(y_tr).value_counts())


        print(f'\n ******************* fold: {fold} ********')
#         print(f'tr size: { len(X_tr)}  val size:  {len(X_val)}')
        xgb_model = xgb.XGBClassifier(**params)
        xgb_model.fit(X_tr,y_tr,
                     verbose=50,
                     eval_set = [(X_val,y_val)],
                     eval_metric='aucpr',
#                     eval_metric = cust_top_n_auc,
                      early_stopping_rounds=50)
        xgb_models.append(xgb_model)
        
        best_iterations.append(xgb_model.get_booster().best_iteration)
        best_n_limit = xgb_model.get_booster().best_ntree_limit
        
        if use_best_iteration:
            val_probs = xgb_model.predict_proba(X_val,
                                               iteration_range=[0,best_n_limit]
#                                                iteration_range=[best_n_limit-1,best_n_limit]
                                               )[:,1]
        else:
            val_probs = xgb_model.predict_proba(X_val)[:,1]
            
        oof_probs[val_index] = val_probs
        
        val_success, val_ratio,val_top_prob_ind,match_pos_arr=get_top_success_count(val_probs,y_val.to_numpy(),
                                                                      top_n=top_n,asc=asc)
        if len(match_pos_arr)==0:
            first_match_pos=11
        else:
            first_match_pos = match_pos_arr[0]
        first_match_positions.append(first_match_pos)
#         print('first_match_pos:',first_match_pos)
        
#         print(f'total:{top_n} success:{val_success} top ratio:{val_ratio}')
        top_ratios.append(val_ratio)
        
        opt_cutoff, f1score = get_opt_cutoff_prec(y_val,val_probs)
#         print('valid cutoff:',opt_cutoff)
        val_cutoffs.append(opt_cutoff)
        opt_cutoff_perc = stats.percentileofscore(val_probs, opt_cutoff, 'weak') / 100
        val_cutoff_percs.append(opt_cutoff_perc)
        
    
        val_labels = convert_probtolabels(val_probs,cutoff=opt_cutoff) 
        mask1 = (val_labels==1)
        mask2 = (y_val==1)
        total = len(val_labels[mask1])
        success = len(val_labels[mask1 & mask2])
        ratio = success/total if total!=0 else 0
#         print(f'ratio: {ratio} total: {total} success: {success}')
        ratios.append(ratio)
        cur_f1 = f1_score(y_val, val_labels,average='macro')
        cur_acc = accuracy_score(y_val,val_labels)
#         print(f'val accuracy score:{cur_acc} f1 score:{cur_f1:.4f}')
        scores.append(cur_acc)
        
        dump_list = xgb_model.get_booster().get_dump()
        cur_iterations = len(dump_list)
        iterations.append(cur_iterations)
#         print('Iteration params:',cur_iterations,xgb_model.get_booster().best_iteration,
#               xgb_model.get_booster().best_ntree_limit)
        
#     print('\ntop ratios:',top_ratios)
    print()
#     print('ratios:',ratios)
#     print('scores:',scores)
#     print('val_cutoffs:',val_cutoffs)
    print('top ratio mean:',np.mean(top_ratios))
    print('first match pos mean:',np.mean(first_match_positions))
    print('ratio mean:',np.mean(ratios))
#     print('score mean:',np.mean(scores))
    mean_cutoff = np.mean(val_cutoffs)
#     print('cutoff mean:',mean_cutoff)
    mean_cutoff_perc= np.mean(val_cutoff_percs)
    
#     print('iterations:',iterations)
    mean_iterations = np.mean(iterations)
#     print('iterations mean:',mean_iterations)
    mean_best_iterations = np.mean(best_iterations)
#     print('best iterations mean:',mean_best_iterations)
#         print(f'total:{top_n} success:{val_success} top ratio:{val_ratio}')

    #oof performance
    oof_success, oof_ratio,oof_top_prob_ind,oof_match_pos_arr=get_top_success_count(oof_probs,y.to_numpy(),
                                                                  top_n=top_n,asc=asc)

    print('oof match positions:',oof_match_pos_arr)
    print('oof top ratio:',oof_ratio)
    
    oof_average_precision = average_precision_score(y.to_numpy(),oof_probs)
    print('oof AUC PR Score:',oof_average_precision)
   
    return xgb_models,top_ratios,mean_iterations,mean_cutoff,mean_cutoff_perc

def gen_top_mean_data_ml_final(test_combined_imp,features_test,
                        n_estimators =100,random_over_sampler=False):
    params = { 'n_estimators':n_estimators,
              'max_leaves':25,
                'subsample':0.8,
              'random_state':145,
              # 'scale_pos_weight': 5,
    #           'max_depth':6,
            'learning_rate':0.05,
             'colsample_bytree':0.6,#0.85,
             'lambda':0.05,
             'alpha':0.1}

    
    X = test_combined_imp[features_test].reset_index(drop=True)
    y = test_combined_imp['target'].reset_index(drop=True)
    oversample = RandomOverSampler(sampling_strategy='minority',random_state=756)    
    if random_over_sampler:
        X , y = oversample.fit_resample(X , y)

    print(f'\n ******************* Finalized Model ********')
    xgb_model = xgb.XGBClassifier(**params)
    xgb_model.fit(X,y)

    
    return xgb_model   

In [31]:
test_all_k_imp[0].head()

roll_actual  \
878          8640   
6523         4463   
2231         9392   
5606         5995   
621           615   

                                                                  seed  \
878   dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
6523  dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
2231  dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
5606  dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   
621   dc7e446233909e175022b03c0da6544670224680264e37ac77ff64b6110f3c22   

                                                                  hash  \
878   3d0099674966d458cb02179e6921e8745afc28bcd265192cefdf3d90ef395189   
6523  3d0099674966d458cb02179e6921e8745afc28bcd265192cefdf3d90ef395189   
2231  3d0099674966d458cb02179e6921e8745afc28bcd265192cefdf3d90ef395189   
5606  3d0099674966d458cb02179e6921e8745afc28bcd265192cefdf3d90ef395189   
621   3d0099674966d458cb02179e6921e8745afc28bcd265192cefdf3d90ef395189   

                                                                               client_seed  \
878   woxpwoxpwoxpwoxpwoxp44b75ada8cef6d618c1503eeffdfe6ce87ca15aae9f9915d737f84f39aa61e62   
6523  woxpwoxpwoxpwoxpwoxpae2f0922066a7df2af477524edb9ddf4ad1d997a581d94335f9600dc0add6efd   
2231  woxpwoxpwoxpwoxpwoxpc821e56e508d046f299f6ddeda39cd8b845a472f7d62b4d6358dd316dac59548   
5606  woxpwoxpwoxpwoxpwoxp0cd076aff36a6b5c2eccca7d0178f78b4295e59205b4c0c5751aa396602f8323   
621   woxpwoxpwoxpwoxpwoxp6a2687f3855b70b004484ffeae9f4b6cc6e547a6af40d74624e05ee4f4007a19   

      client_index  roll_0  roll_1  roll_2  roll_3  roll_4  roll_5  roll_6  \
878         882369    8007    5539    6100    2476    5044    6500    5753   
6523        180625    6005     586    2049    3578     711    6819    9638   
2231        710048    3002    7439    4590    4424    4648     259    7920   
5606        289724    9006    2416    7705    6972    9879    4762    7479   
621         917830    3003      31    8828    3185    5661    9932    4740   

      roll_7  roll_8  roll_9  roll_10  roll_11  roll_12  roll_13  roll_14  \
878     1881    3695    4265     8878     3668     7109     2872     3249   
6523    4677    7749    3858      746     9889     2531     7569     8635   
2231    2852    1551    1118      182     5821     4039     3652     8111   
5606    7882    3519    4542     3588     1626     8924     2351     7848   
621     5574    8690    8609     6000     8850     5455     2453     9296   

      roll_15  roll_16  roll_17  roll_18  roll_19  roll_20  roll_21  roll_22  \
878      3312     4663     5955     2368      741     6044     4280     4101   
6523     2178     3132      934     7040     6507     6254     9835      168   
2231     5769     9659     2029     5120     6108     9862     7374     3133   
5606     2219     1725     5306     7840     6610     4076     8023     3791   
621      6988     9230     2382     9590     7431     4543     5997     4149   

      roll_23  roll_24  roll_25  roll_26  roll_27  roll_28  roll_29  roll_30  \
878      1711     3107     1126     4793      419     4565     6892     3966   
6523     3141     6065     2852     8257     1431     4573     7270     4154   
2231     2254     7343     6194     7512     8307     5977     4439     8434   
5606      532     3242     1716     5015     8360     6946     4478     5979   
621      5129     6291     6525     2201     3296     3506     7372     1045   

      roll_31  roll_32  roll_33  roll_34  roll_35  roll_36  roll_37  roll_38  \
878      5936     6578     7552     6966     3928     5518     9123     8640   
6523     3968     4075     9349     2164     6373      865     8498     5405   
2231     6906     2001     9995     4699     8448     8702     7523     3596   
5606     4100     1873     3374      418     7926     2279     9610     7906   
621      1539     6613     1533     9256     9680     9582     4442      348   

      roll_39  roll_40  roll_41  roll_42  roll_43

In [32]:

if HIGH_ANALYSIS:
    mask = test_all_k['roll_actual']>HIGH_TARGET
else:
    mask = test_all_k['roll_actual']<LOW_TARGET
    
test_all_k['target']=0
test_all_k.loc[mask,'target']=1

y_test = test_all_k['target']


test_combined_imp=pd.concat(test_all_k_imp,axis=0)
if HIGH_ANALYSIS:
    mask = test_combined_imp['roll_actual']>HIGH_TARGET
else:
    mask = test_combined_imp['roll_actual']<LOW_TARGET
    
test_combined_imp['target']=0
test_combined_imp.loc[mask,'target']=1

print(len(test_all_k))
print(len(test_combined_imp))

63
329


In [49]:
# test_temp = test.sample(n=100,random_state=100).copy()

# if HIGH_ANALYSIS:
#     mask = test_temp['roll_actual']>HIGH_TARGET
# else:
#     mask = test_temp['roll_actual']<LOW_TARGET
    
# test_temp['target']=0
# test_temp.loc[mask,'target']=1

# test_temp['k']=-1
# y_test = test_temp['target']

In [50]:
# test_temp = test_all_k.copy()

In [51]:
# %%time

# cur_feats_count = 5
# cur_features = [col for col in imp_df['feature'].values if (col.startswith('roll_'))][:cur_feats_count]
# cur_features += [col for col in imp_df['feature'].values if (col.startswith('count_'))][:5]

# # cur_features = features_test.copy()
# test_combined_imp= get_sim_summary(test_combined_imp,df,
#                                      True,cur_feats_count)
# # cur_features += ['ratio_mean_summary','roll_mean_summary']
# cur_features += ['ratio_mean_rank','roll_mean_rank']
# # cur_features += ['ratio_mean_rank','roll_mean_rank','ratio_group_roll_rank']
# print(cur_features)
# xgb_models,top_ratios,mean_iterations,mean_cutoff,mean_cutoff_perc = gen_top_mean_data_ml(test_combined_imp,cur_features,n_estimators=1000)
# # print(mean_cutoff_perc)


In [52]:
# # test_temp = test.sample(n=100).copy()
# # test_temp = test_all_k.copy()

# test_all_k= get_sim_summary(test_all_k,df,
#                             True,cur_feats_count)

# test_probs= np.zeros(len(test_all_k))
# for model in xgb_models:
#     test_probs += (model.predict_proba(test_all_k[cur_features])[:,1]) 
# test_probs = test_probs / len(xgb_models)
# top_n=10
# test_success, test_ratio,test_top_prob_ind,match_pos_arr=get_top_success_count(test_probs,y_test.to_numpy(),
#                                                                   top_n=top_n,asc=False)
# print(f'total:{top_n} success:{test_success} top ratio:{test_ratio} match positions: {match_pos_arr}')

# #threshold based

# mean_cutoff_perc_based = np.quantile(test_probs, mean_cutoff_perc)
# print(mean_cutoff_perc_based,mean_cutoff)

# test_labels = convert_probtolabels(test_probs,cutoff=mean_cutoff) 
# mask1 = (test_labels==1)
# mask2 = (y_test==1)
# total = len(test_labels[mask1])
# success = len(test_labels[mask1 & mask2])
# ratio = success/total if total!=0 else 0
# print(f'ratio: {ratio} total: {total} success: {success}')

In [53]:

# # test_temp = test.sample(n=100).copy()
# # test_temp = test_all_k.copy()

# test_all_k= get_sim_summary(test_all_k,df,
#                             True,cur_feats_count)
# model_final = gen_top_mean_data_ml_final(test_combined_imp,cur_features,
#                         n_estimators = int(mean_iterations))

# test_probs = (model_final.predict_proba(test_all_k[cur_features])[:,1]) 
# top_n=10
# test_success, test_ratio,test_top_prob_ind,match_pos_arr=get_top_success_count(test_probs,y_test.to_numpy(),
#                                                                   top_n=top_n,asc=False)
# print(f'total:{top_n} success:{test_success} top ratio:{test_ratio} match positions: {match_pos_arr}')
# #threshold based
# mean_cutoff_perc_based = np.quantile(test_probs, mean_cutoff_perc)
# print(mean_cutoff_perc_based,mean_cutoff)

# test_labels = convert_probtolabels(test_probs,cutoff=mean_cutoff_perc_based) 
# mask1 = (test_labels==1)
# mask2 = (y_test==1)
# total = len(test_labels[mask1])
# success = len(test_labels[mask1 & mask2])
# ratio = success/total if total!=0 else 0
# print(f'ratio: {ratio} total: {total} success: {success}')

In [57]:
x=[]
for i in range(5):
    x.append([]) 
print(x)
print(x[1])
x[1].append([5,32])
print(x[0])
# x[1]+=[5,32]
# x[2]+=[17,52]
x

[[], [], [], [], []]
[]
[]


[[], [[5, 32]], [], [], []]

In [149]:
def random_experiment(data,probs,count_fetch=10, iterations=1000):
    data['probs_new']=probs
    
    success_count=0
    success_presence=0
#     mask=data['roll_actual']<LOW_TARGET
    mask=create_target_mask(data)
    print(f'All: {len(data)} All Success: {len(data[mask])}')
    for i in range(iterations):
        data_sample = data.sample(n=count_fetch,random_state=i+random.randint(1,1000))
        mask = create_target_mask(data_sample)
        if len(data_sample[mask])!=0:
            success_presence +=1
        
#         data_top  = data_sample[data_sample['probs_new']>=data_sample['probs_new'].nlargest(5).min()]
#         data_top  = data_sample[(data_sample['probs_new']<=data_sample['probs_new'].nlargest(4).min())
#                                & (data_sample['probs_new']>=data_sample['probs_new'].nlargest(7).min())]
        large_index = int(len(data) / 4)
        data_top  = data[(data['probs_new']>=data['probs_new'].nlargest(large_index).min())]
#         data_top  = data_sample[(data_sample['probs_new']>=data_sample['probs_new'].nlargest(large_index).min())]
#         data_top  = data_sample[data_sample['probs_new']==data_sample['probs_new'].max()]
        mask = create_target_mask(data_top)
        success_count +=len(data_top[mask])
        
    print(f'total success: {success_count} and total presence: {success_presence} out of {iterations} experiments')
    
    data = data.drop('probs_new',axis=1)
    

In [150]:
%%time

use_best_iteration=False
is_rank_pct=True
cur_feats_count = 2
top_order_asc = False
top_n=20
random_over_sampler=False
n_splits=5

rand_count_fetch=10
rand_iterations=1000


first_match_success_total=0
match_count_success_total=0
first_match_success_total_final=0
match_count_success_total_final=0

first_match_success_nonces=[]
match_count_success_nonces=[]
first_match_success_nonces_final=[]
match_count_success_nonces_final=[]

# nonce_models=[[]]*len(k_obj_all_nonces)

nonce_models=[]
for i in range(len(k_obj_all_nonces)):
    nonce_models.append([]) 
    
for i,k_obj in enumerate(k_obj_all_nonces):
    
    
    test_all_k_imp,test_all_k,df,features_test,all_k,top_k_ele,all_k_imp,top_k_ele_imp,imp_df = k_obj
    
    print(f'\n****************** NONCE {nonce_list[i]} initial success {len(top_k_ele)} out of {len(all_k)} ****************** ')

    cur_feats_count=140

    for test_hash_imp in test_all_k_imp:
        test_hash_imp= get_sim_summary(test_hash_imp,df,
                                       True,cur_feats_count,is_rank_pct=is_rank_pct)

    if HIGH_ANALYSIS:
        mask = test_all_k['roll_actual']>HIGH_TARGET
    else:
        mask = test_all_k['roll_actual']<LOW_TARGET

    test_all_k['target']=0
    test_all_k.loc[mask,'target']=1

    y_test = test_all_k['target']


    test_combined_imp=pd.concat(test_all_k_imp,axis=0)
    if HIGH_ANALYSIS:
        mask = test_combined_imp['roll_actual']>HIGH_TARGET
    else:
        mask = test_combined_imp['roll_actual']<LOW_TARGET

    test_combined_imp['target']=0
    test_combined_imp.loc[mask,'target']=1

    print(len(test_all_k))
    print(len(test_combined_imp))



    # for cur_feats_count in [2]+ list(range(5,61,5)):
    for cur_feats_count in  [140]:

        print(f'\n******************** Feats Count {cur_feats_count} ********************')

        cur_features = [col for col in imp_df['feature'].values if (col.startswith('roll_'))][:cur_feats_count]
        cur_features += [col for col in imp_df['feature'].values if (col.startswith('count_'))][:5]

        cur_features = features_test.copy()
#         test_combined_imp= get_sim_summary(test_combined_imp,df,
#                                              True,cur_feats_count,is_rank_pct=is_rank_pct)
    #     cur_features += ['ratio_mean','roll_mean']
    #     cur_features += ['ratio_mean_rank','roll_mean_rank']
        roll_cols = [col for col in imp_df['feature'].values if (col.startswith('roll_'))][:cur_feats_count]
        rank_cols = [f'{col}_rank' for col in roll_cols]
#         cur_features += rank_cols
        cur_features += [
    #                         'probs_rank',
#                         'ratio_mean_rank','roll_mean_rank','ratio_group_roll_rank',
    #                     'ratio_group_probs_rank',
    #                     'ratio_group_roll_rank_desc'
                        ]
    #     print(cur_features)
        cur_models,top_ratios,mean_iterations,mean_cutoff,mean_cutoff_perc = \
                                                    gen_top_mean_data_ml(test_combined_imp,
                                                                           cur_features,
                                                                            n_estimators=5000,
                                                                             asc=top_order_asc,top_n=top_n,
                                                                            random_over_sampler=random_over_sampler,
                                                                        use_best_iteration=use_best_iteration,
                                                                        n_splits=n_splits)

        # test_temp = test.sample(n=100).copy()
        # test_temp = test_all_k.copy()

        test_all_k= get_sim_summary(test_all_k,df,
                                    True,cur_feats_count,is_rank_pct=is_rank_pct)

        test_probs= np.zeros(len(test_all_k))
        
        nonce_models[i]+=cur_models
        print('models length:',i,len(nonce_models[i]))
        
#         max_score = 0
#         best_models=[]
#         for model_no,model in enumerate(nonce_models[i]):
#             cur_score = model.best_score
#             if cur_score > max_score:
#                 best_score = cur_score
#                 best_model_no = model_no
#             if cur_score>=0.2:
#                 best_models.append(model_no)
                
#         if len(best_models)==0:
#             best_models.append(best_model_no)
            
#         print(f'best models:{best_models}')
#         for model_no in best_models:
#             model = nonce_models[i][model_no]
#             test_probs += (model.predict_proba(test_all_k[cur_features])[:,1]) 
            
#         test_probs = test_probs / len(best_models)
        
        for model in nonce_models[i]:
#             model = nonce_models[i][0]
            print(f'Best SCORE: {model.best_score} Best ITERATION: {model.best_iteration},{model.get_booster().best_ntree_limit}')
            if use_best_iteration:
#                 test_probs += (model.predict_proba(test_all_k[cur_features],
#                               iteration_range=[model.get_booster().best_ntree_limit-1,
#                                                model.get_booster().best_ntree_limit])[:,1]) 
                test_probs += (model.predict_proba(test_all_k[cur_features],
                              iteration_range=[0,
                                               model.get_booster().best_ntree_limit])[:,1]) 
            else:
                test_probs += (model.predict_proba(test_all_k[cur_features])[:,1]) 

            
        test_probs = test_probs / len(nonce_models)
        
        average_precision = average_precision_score(test_all_k['target'], test_probs)
        print(f'AUC PR Score:{average_precision}')
        
#         random_experiment(test_all_k,test_probs,count_fetch=rand_count_fetch, iterations=rand_iterations)
        
        test_success, test_ratio,test_top_prob_ind,match_pos_arr=get_top_success_count(test_probs,y_test.to_numpy(),
                                                                          top_n=top_n,asc=top_order_asc)
        print(f'total:{top_n} success:{test_success} top ratio:{test_ratio} match positions: {match_pos_arr}')
        
        if (len(match_pos_arr)!=0) and (match_pos_arr[0] <= 5):
            first_match_success_total+=1
            first_match_success_nonces.append(nonce_list[i])
        
        if len(match_pos_arr) >=3:
            match_count_success_total+=1
            match_count_success_nonces.append(nonce_list[i])

        #threshold based
        test_labels = convert_probtolabels(test_probs,cutoff=mean_cutoff) 
        mask1 = (test_labels==1)
        mask2 = (y_test==1)
        total = len(test_labels[mask1])
        success = len(test_labels[mask1 & mask2])
        ratio = success/total if total!=0 else 0
        print(f'ratio: {ratio} total: {total} success: {success}')


        #Final Model

        test_all_k= get_sim_summary(test_all_k,df,
                                    True,cur_feats_count,is_rank_pct=is_rank_pct)
        model_final = gen_top_mean_data_ml_final(test_combined_imp,cur_features,
                                n_estimators = int(mean_iterations),random_over_sampler=random_over_sampler)

        test_probs = (model_final.predict_proba(test_all_k[cur_features])[:,1]) 
        average_precision = average_precision_score(test_all_k['target'], test_probs)
        print(f'AUC PR Score:{average_precision}')
#         random_experiment(test_all_k,test_probs,count_fetch=rand_count_fetch, iterations=rand_iterations)
#         test_probs += (model_final.predict_proba(test_all_k[cur_features])[:,1]) 
#         test_probs = test_probs / 2

        
        test_success, test_ratio,test_top_prob_ind,match_pos_arr=get_top_success_count(test_probs,y_test.to_numpy(),
                                                                          top_n=top_n,asc=top_order_asc)
        print(f'total:{top_n} success:{test_success} top ratio:{test_ratio} match positions: {match_pos_arr}')
        
        if (len(match_pos_arr)!=0) and (match_pos_arr[0] <= 5):
            first_match_success_total_final+=1
            first_match_success_nonces_final.append(nonce_list[i])
        
        if len(match_pos_arr) >=3:
            match_count_success_total_final+=1
            match_count_success_nonces_final.append(nonce_list[i])

        #threshold based
        mean_cutoff_perc_based = np.quantile(test_probs, mean_cutoff_perc)
    #     print(mean_cutoff_perc_based,mean_cutoff)

        test_labels = convert_probtolabels(test_probs,cutoff=mean_cutoff_perc_based) 
        mask1 = (test_labels==1)
        mask2 = (y_test==1)
        total = len(test_labels[mask1])
        success = len(test_labels[mask1 & mask2])
        ratio = success/total if total!=0 else 0
        print(f'ratio: {ratio} total: {total} success: {success}')
        
print('****************************  SUMMARY ********************************')
print('-------------- Normal Matches -----------------------')
print(f'Top Success: {first_match_success_total} Count Success: {match_count_success_total}')
print(f'Top Success Nonces: {first_match_success_nonces}')
print(f'Count Success Nonces: {match_count_success_nonces}')
print('-------------- Final Matches -----------------------')
print(f'Top Success: {first_match_success_total_final} Count Success: {match_count_success_total_final}')
print(f'Top Success Nonces: {first_match_success_nonces_final}')
print(f'Count Success Nonces: {match_count_success_nonces_final}')



****************** NONCE 2673 initial success 9 out of 62 ****************** 
62
319

******************** Feats Count 140 ********************

 ******************* fold: 0 ********
[0]	validation_0-aucpr:0.26251
[50]	validation_0-aucpr:0.25048
[51]	validation_0-aucpr:0.25487

 ******************* fold: 1 ********
[0]	validation_0-aucpr:0.10011
[49]	validation_0-aucpr:0.09118

 ******************* fold: 2 ********
[0]	validation_0-aucpr:0.09635
[50]	validation_0-aucpr:0.12308
[52]	validation_0-aucpr:0.12007

 ******************* fold: 3 ********
[0]	validation_0-aucpr:0.07686
[50]	validation_0-aucpr:0.10805
[51]	validation_0-aucpr:0.10760

 ******************* fold: 4 ********
[0]	validation_0-aucpr:0.07508
[50]	validation_0-aucpr:0.10940
[53]	validation_0-aucpr:0.10531

top ratio mean: 0.11000000000000001
first match pos mean: 5.0
ratio mean: 0.2785714285714286
oof match positions: [ 3  4 10 14 18]
oof top ratio: 0.25
oof AUC PR Score: 0.14670016608922096
models length: 0 5
Best SCO

[50]	validation_0-aucpr:0.06533
[78]	validation_0-aucpr:0.05948

 ******************* fold: 1 ********
[0]	validation_0-aucpr:0.10333
[50]	validation_0-aucpr:0.08476
[100]	validation_0-aucpr:0.08916
[131]	validation_0-aucpr:0.10556

 ******************* fold: 2 ********
[0]	validation_0-aucpr:0.16613
[50]	validation_0-aucpr:0.11260
[56]	validation_0-aucpr:0.09870

 ******************* fold: 3 ********
[0]	validation_0-aucpr:0.12381
[50]	validation_0-aucpr:0.07237

 ******************* fold: 4 ********
[0]	validation_0-aucpr:0.09473
[50]	validation_0-aucpr:0.06960

top ratio mean: 0.14
first match pos mean: 6.4
ratio mean: 0.2634199134199134
oof match positions: [ 5 20]
oof top ratio: 0.1
oof AUC PR Score: 0.0987083677528579
models length: 4 5
Best SCORE: 0.085178 Best ITERATION: 28,29
Best SCORE: 0.214512 Best ITERATION: 82,83
Best SCORE: 0.338223 Best ITERATION: 6,7
Best SCORE: 0.123813 Best ITERATION: 0,1
Best SCORE: 0.113284 Best ITERATION: 1,2
AUC PR Score:0.2161355637657219
All: 1

[50]	validation_0-aucpr:0.10263
[100]	validation_0-aucpr:0.14917
[150]	validation_0-aucpr:0.24413
[190]	validation_0-aucpr:0.14295

 ******************* fold: 3 ********
[0]	validation_0-aucpr:0.07542
[50]	validation_0-aucpr:0.08551
[63]	validation_0-aucpr:0.09428

 ******************* fold: 4 ********
[0]	validation_0-aucpr:0.14951
[50]	validation_0-aucpr:0.29124
[81]	validation_0-aucpr:0.27852

top ratio mean: 0.13999999999999999
first match pos mean: 1.4
ratio mean: 0.22000000000000003
oof match positions: [ 2  7 10]
oof top ratio: 0.15
oof AUC PR Score: 0.13684368910501565
models length: 8 5
Best SCORE: 0.146283 Best ITERATION: 13,14
Best SCORE: 0.298995 Best ITERATION: 4,5
Best SCORE: 0.248244 Best ITERATION: 141,142
Best SCORE: 0.223525 Best ITERATION: 14,15
Best SCORE: 0.366074 Best ITERATION: 31,32
AUC PR Score:0.22385752141706755
All: 67 All Success: 8
total success: 4000 and total presence: 776 out of 1000 experiments
total:20 success:4 top ratio:0.2 match positions: [ 4  5 1

[101]	validation_0-aucpr:0.07920

 ******************* fold: 3 ********
[0]	validation_0-aucpr:0.28341
[50]	validation_0-aucpr:0.12738
[56]	validation_0-aucpr:0.13916

 ******************* fold: 4 ********
[0]	validation_0-aucpr:0.07192
[50]	validation_0-aucpr:0.07185
[54]	validation_0-aucpr:0.07380

top ratio mean: 0.1
first match pos mean: 7.0
ratio mean: 0.0901068376068376
oof match positions: [13 15 20]
oof top ratio: 0.15
oof AUC PR Score: 0.09851500966346868
models length: 12 5
Best SCORE: 0.076016 Best ITERATION: 8,9
Best SCORE: 0.076467 Best ITERATION: 0,1
Best SCORE: 0.091327 Best ITERATION: 51,52
Best SCORE: 0.331866 Best ITERATION: 6,7
Best SCORE: 0.111615 Best ITERATION: 5,6
AUC PR Score:0.3552287581699346
All: 62 All Success: 4
total success: 2000 and total presence: 531 out of 1000 experiments
total:20 success:3 top ratio:0.15 match positions: [ 1 15 17]
ratio: 0 total: 0 success: 0

 ******************* Finalized Model ********
[10:08:41] WARNING: /home/conda/feedstock_r

[50]	validation_0-aucpr:0.10776
[56]	validation_0-aucpr:0.10668

 ******************* fold: 4 ********
[0]	validation_0-aucpr:0.11990
[50]	validation_0-aucpr:0.12262
[52]	validation_0-aucpr:0.14052

top ratio mean: 0.17
first match pos mean: 4.4
ratio mean: 0.21255411255411255
oof match positions: [2 4 6]
oof top ratio: 0.15
oof AUC PR Score: 0.1552827282989584
models length: 16 5
Best SCORE: 0.168059 Best ITERATION: 119,120
Best SCORE: 0.230772 Best ITERATION: 0,1
Best SCORE: 0.153957 Best ITERATION: 2,3
Best SCORE: 0.142953 Best ITERATION: 7,8
Best SCORE: 0.184688 Best ITERATION: 2,3
AUC PR Score:0.3628891225546736
All: 54 All Success: 12
total success: 4000 and total presence: 943 out of 1000 experiments
total:20 success:5 top ratio:0.25 match positions: [ 1  3  9 13 19]
ratio: 0 total: 0 success: 0

 ******************* Finalized Model ********
[10:09:05] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1645117766796/work/src/learner.cc:1115: Starting in XGBoost 1.

In [129]:
k_ob

NameError: name 'k_ob' is not defined

In [127]:
test_combined_imp['roll_actual'].head(5)

roll_actual  roll_actual  roll_actual  roll_actual  roll_actual
5758        251.0          NaN          NaN          NaN          NaN
4184        716.0          NaN          NaN          NaN          NaN
478         355.0       4754.0          NaN          NaN          NaN
835         147.0          NaN          NaN          NaN          NaN
4293        330.0          NaN          NaN          NaN          NaN

In [ ]:
    
def create_cutoff_pos_df_ml(test_filt_all_k,test_all_k_imp,
                            features_test,test_hash_cutoff_df,
                         imp_feats_count_list,
                         test_ratio_limit=0.12,
                         top_k_ele=None)

    for i,imp_feats_count in enumerate(imp_feats_count_list):
        test_filt_all_k= get_sim_summary(test_filt_all_k,
                                     True,imp_feats_count)
        
        print('--- Top 5 data ---')
        print(top_mean_data[:5])

        top_mean_data_list.append(top_mean_data)

        if top_k_ele is not None:
            print(f'\n******success data *****')
            mask= top_mean_data['k'].isin(top_k_ele)
            print(top_mean_data[mask])
            print(f'\n******success positions *****')
            cur_positions = list(top_mean_data[mask].index+1)
            print(cur_positions)

        
    return top_mean_data_list

In [109]:
import math

def get_test_sel_cutoff_pos(test_probs,models,features_test,test_hash_cutoff_df,
                            cutoff_pos_df_hash,
                            is_min_total=False,total_cri=2,top_n=10,
                           sim_cutoff_dfs=None,imp_feats_count_list=None):
    cutoff_pos_stat = cutoff_pos_df_hash.groupby(['imp_feats_count'])['match_pos_1',
                                               'match_total_top_5',
                                               'match_total_top_10'].mean().reset_index()
    print(' ........... Overall Positions of Features .........')
    print(cutoff_pos_stat)
    cutoff_pos_df_hash_filt=cutoff_pos_df_hash[cutoff_pos_df_hash['condn_max']==False]
    cutoff_pos_stat = cutoff_pos_df_hash_filt.groupby(['imp_feats_count'])['match_pos_1',
                                               'match_total_top_5',
                                               'match_total_top_10'].mean().reset_index()
    print(' ........... Low Positions of Features .........')
    print(cutoff_pos_stat)
    cutoff_pos_best= cutoff_pos_stat.sort_values(['match_pos_1','match_total_top_5'],
                                                ascending=[True,False])\
                                    .reset_index().iloc[0]
    print('*** Best cutoff position in hash **** ')
    print(cutoff_pos_best)
    predicted_raw_pos=cutoff_pos_best['match_pos_1']
    predicted_max_pos = math.ceil(predicted_raw_pos)
    
    if predicted_raw_pos==predicted_max_pos:
        predicted_max_pos+=1
    
    is_imp_feats=True
    imp_feats_count=cutoff_pos_best['imp_feats_count']
    is_min_total=False
    
    if sim_cutoff_dfs is None:
        sim_cutoff_df,test_probs= get_sim_cutoff_data(test_probs,models,features_test,test_hash_cutoff_df,
                                                 is_imp_feats,imp_feats_count,gen_probs=False)
    else:
        #to use existing buffer, read the matching sim cutoff df from the list of buffer
        idx = imp_feats_count_list.index(imp_feats_count)
        sim_cutoff_df=sim_cutoff_dfs[idx]

    top_mean_data = get_hash_prob_top_data(test_probs,models,features_test,
                           test_hash_cutoff_df,is_imp_feats,imp_feats_count,
                           sim_cutoff_df = sim_cutoff_df,
                            is_min_total=is_min_total, total_cri=total_cri,
                            top_n=top_n)
    
    top_mean_data['rank']=top_mean_data['ratio_mean'].rank(method='min',ascending=False)
    mask = (top_mean_data['rank']<=predicted_max_pos) & (top_mean_data['ratio_mean']>0)
    top_mean_sel = top_mean_data[mask]
    k_sel_list = list(top_mean_sel['k'].values)
    print(top_mean_data)
    print(top_mean_sel)
    print(f'{k_sel_list=}')
    

#     mask = cutoff_pos_df_actual['imp_feats_count']==cutoff_pos_best['cutoff_pos_best']
#     mask2 = cutoff_pos_df_actual['match_pos_1']<=predicted_max_pos
#     k_sel = cutoff_pos_df_actual.loc[mask & mask2, 'k' ]
    
    test_sel  = None
    for k_sel in k_sel_list:
        row = test_hash_cutoff_df.loc[k_sel]
    #     print(row)
        mask = (test_probs['probs']>=row['cutoff']) & (test_probs['probs']<=row['cutoff_2'])
        cur_test_sel = test_probs[mask]
        cur_test_sel['k']=k_sel
        if test_sel is None:
            test_sel = cur_test_sel
        else:
            test_sel = pd.concat([test_sel,cur_test_sel],axis=0)
        print('Test Size:',len(test_sel))

    return k_sel_list,test_sel,top_mean_sel



In [110]:
# k_sel_list=[218,198,201,190,184]
# print(df[df.index.isin(k_sel_list)])
# test_temp=None
# for k_sel in k_sel_list:
#     row = df.loc[k_sel]
# #     print(row)
#     mask = (test['probs']>=row['cutoff']) & (test['probs']<=row['cutoff_2'])
#     cur_test_sel = test[mask]
#     cur_test_sel['k']=k_sel
#     if test_temp is None:
#         test_temp = cur_test_sel
#     else:
#         test_temp = pd.concat([test_temp,cur_test_sel],axis=0)

# cols = [col for col in imp_df['feature'].values if (col.startswith('roll_'))][:20]        
# # test_temp
# test_temp['feats_mean']=test_temp[cols].mean(axis=1)
# test_temp['feats_std']=test_temp[cols].std(axis=1)
# test_temp['feats_count']=(test_temp[cols]<1000).sum(axis=1)
# test_temp[['k','roll_actual','feats_mean','feats_std','feats_count']+cols]

In [111]:
# test_orig= test.copy()
# test_hash_orig = test_hash.copy()

In [112]:
count_all_k = len(all_k)
if count_all_k<10:
    print(f'PROJECT WARNING: number of target records is {count_all_k} which is less than 10 ')
count_top_k = len(top_k)    
if count_top_k<2:
    print(f'PROJECT WARNING: number of probable success is {count_top_k} which is less than 2')  
hash_success = len(df[(df['total']==2) & (df['ratio']>0)])    
if hash_success<2:
    print(f'PROJECT WARNING: number of hash success is {hash_success} which is less than 2')

In [113]:
print(len(test))
mask = test.duplicated(subset='client_seed')
print(len(test[mask]))
print(test[mask]['client_seed'].nunique())

print(len(test_hash))
mask = test_hash.duplicated(subset='client_seed')
print(len(test_hash[mask]))
print(test_hash[mask]['client_seed'].nunique())

8019
0
0
7968
0
0


In [114]:
# test=test.drop_duplicates(subset='client_seed')
# test_hash=test_hash.drop_duplicates(subset='client_seed')

In [115]:
# %%time
# sim_cutoff_dfs_temp=None
# imp_feats_count_list = [2,5,10,15,20,25,30,40]
# cutoff_pos_df_temp,sim_cutoff_dfs_temp,test_probs=create_cutoff_pos_df(test,xgb_models,
#                     features_test,df[df.index.isin([2,22,70,100,178,200,486,
#                                                     488,525,604,672,681,747,
#                                                    812,1212,1392,1536])],
#                     imp_feats_count_list,is_compute_matches=False,
#                    test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs_temp,
#                     low_high_record_condns=[(False,2,20)])
# cutoff_pos_df_temp

In [116]:
# %%time
# imp_feats_count_list = [30,40]
# sim_cutoff_dfs=None
# cutoff_pos_df_hash,sim_cutoff_dfs,test_probs_hash=create_cutoff_pos_df(test_hash,xgb_models,
#                     features_test,df[df['total']<=10],
#                     imp_feats_count_list,
#                    test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs,
#                     low_high_record_condns=[(False,10,20),(False,2,20)])
# cutoff_pos_df_hash

In [117]:
# cutoff_pos_df_hash[cutoff_pos_df_hash['condn_val']==2]

In [118]:
# print(len(df))
# df_filt = df[(df['total']>=50)]
# print(len(df_filt))
# # df_filt[df_filt['ratio']==0.12]

In [119]:
# %%time
# imp_feats_count_list = [2,5,10,15,20,25,30,40]
# sim_cutoff_dfs=None
# min_normal_count=50
# max_low_count = 5
# cutoff_pos_df_hash,sim_cutoff_dfs,test_probs_hash=create_cutoff_pos_df(test_hash,xgb_models,
#                     features_test,df[(df['total']<=max_low_count) | (df['total']>=min_normal_count)],
#                     imp_feats_count_list,
#                    test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs,
#                     low_high_record_condns=[(True,min_normal_count,10),
#                                             (False,max_low_count,20),(False,2,20)])
# cutoff_pos_df_hash

In [120]:
# cutoff_pos_df_hash[cutoff_pos_df_hash['condn_val']==2]

In [121]:
print(all_k)
print(top_k_ele)

[4, 13, 23, 26, 28, 30, 31, 63, 376, 389, 405, 408, 413, 415, 416, 417, 421, 424, 427, 429, 433, 442, 444, 445, 453, 458, 459, 460, 462, 463, 468, 472, 477, 478, 485, 487, 489, 492, 494, 496, 498, 502, 503, 507, 508, 509, 518, 523, 529, 530, 544, 546, 550, 554, 569, 570, 572, 580, 583, 598, 609, 617, 619, 628]
[417, 427, 459, 463, 468, 485, 489, 544, 617]


In [122]:
# %%time
# imp_feats_count_list = [2,5,10,15,20,25,30,35,40,45,50,55,60]
# sim_cutoff_dfs=None
# cutoff_pos_df_hash,sim_cutoff_dfs,test_probs_hash=create_cutoff_pos_df(test_hash,xgb_models,
#                     features_test,df[(df['total']==1)],
#                     imp_feats_count_list,
#                    test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs,
#                     low_high_record_condns=[(False,1,20)])
# cutoff_pos_df_hash

In [123]:
# temp=df.loc[[243,181,220,226,245,10,4]]
# temp['diff']=(df.loc[214,'cutoff']-temp['cutoff']).abs()
# temp.sort_values('diff')

In [124]:
# # set(top_mean_data_actual[0]['k']).intersection(set(top_k_ele))

# for i in range(13):
#     cur_top_data = top_mean_actual[i]
#     print(f'******{imp_feats_count_list[i]=}*****')
#     print(cur_top_data[cur_top_data['k'].isin(top_k_ele)])
#     print(cur_top_data[cur_top_data['k'].isin(top_k_ele)].index+1)

Check top important hash test data for ascending or descending ratio mean performance

In [125]:
# ROLL_MEAN_ASC = True

In [126]:
%%time
# imp_feats_count_list = [2,5,10,15,20,25,30,35,40,45,50,55,60]
# imp_feats_count_list= [2]+list(range(5,201,5))
imp_feats_count_list= list(range(2,151))

# imp_feats_count_list = [2,5]
imp_feats_size = len(imp_feats_count_list)
first_match_pos_arr= np.zeros((hash_imp_count,2,imp_feats_size))
dictionary_list=[]
for hash_idx in range(hash_imp_count):
    top_n = len(all_k_imp[hash_idx])
    print(f'\ntop_n:{top_n}')
    for ratio_mean_order in [False,True]:
        for roll_mean_order in [False,True]:
            print(f'********************** Test Hash {hash_imp_names[hash_idx]} ratio_mean order {ratio_mean_order}***********************')
            sim_cutoff_dfs_actual=None
            cutoff_pos_df_actual,sim_cutoff_dfs_actual,top_mean_actual=create_cutoff_pos_df(test_hash_imp[hash_idx],xgb_models,
                                features_test,df[df.index.isin(all_k_imp[hash_idx])],
                                imp_feats_count_list,test_all_k_imp[hash_idx],is_compute_matches=False,
                               test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs_actual,
                                low_high_record_condns=[(False,1,top_n)],
                                ratio_mean_asc=ratio_mean_order,
                                roll_mean_asc=roll_mean_order
                                )

            first_match_pos_list=[]
            match_pos_list=[]
            for feats_idx in range(imp_feats_size):
                cur_top_data = top_mean_actual[feats_idx]
                print(f'\n******{imp_feats_count_list[feats_idx]} feats success data *****')
                mask= cur_top_data['k'].isin(top_k_ele_imp[hash_idx])
                print(cur_top_data[mask])
                cur_positions = list(cur_top_data[mask].index+1)

                dictionary_data = {'imp_feats_count': imp_feats_count_list[feats_idx],
                                   'hash_index':hash_idx, 
                                   'hash_feat_name': hash_imp_names[hash_idx], 
                                    'ratio_mean_asc':ratio_mean_order,
                                    'roll_mean_asc':roll_mean_order,
                                    'first_match_pos':cur_positions[0],
                                    'other_match_pos':cur_positions[1:]
                      }
                dictionary_list.append(dictionary_data)
                print(f'\n {imp_feats_count_list[feats_idx]} feats success positions')
                print(cur_positions)
        
        
match_pos_df = pd.DataFrame.from_dict(dictionary_list)
match_pos_df        


top_n:61
********************** Test Hash roll_10_nonce ratio_mean order False***********************
max_good_k=364

********************** Feature count 2 *****************
******* Condition (False, 1, 61) for feature count 2 *****************
imp_feats_count: 2
[['roll_std_50_60_nonce', 'roll_10_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0  476         0.5  2169.742283
1  485         0.5  1828.941574
2    6         0.5  1358.446095
3  500         0.5  1237.174575
4  582         0.0  6740.886120

********************** Feature count 3 *****************
******* Condition (False, 1, 61) for feature count 3 *****************
imp_feats_count: 3
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0  485    0.666667  1398.294383
1  442    0.333333  4152.697257
2  548    0.333333  3908.234421
3  484    0.333333  3887.010743
4    6    0.333333  3570.297397

********************** Feature count 4 *****************
*

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  402    0.294118  3949.349308
1  485    0.176471  4580.097705
2  524    0.176471  4540.313980
3  407    0.176471  4394.535897
4  501    0.176471  4239.852448

********************** Feature count 18 *****************
******* Condition (False, 1, 61) for feature count 18 *****************
imp_feats_count: 18
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0  402    0.277778  3937.829902
1  485    0.166667  4731.536722
2  501    0.166667  4518.749534
3  450    0.166667  4487.296597
4  391    0.166667  4407.764219

********************** Feature count 19 *****************
******* Condition (False, 1, 61) for featu


********************** Feature count 30 *****************
******* Condition (False, 1, 61) for feature count 30 *****************
imp_feats_count: 30
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0  402    0.333333  3782.031274
1  485    0.200000  4767.055366
2  501    0.166667  4466.492145
3  415    0.166667  4324.318786
4  536    0.166667  4307.917671

********************** Feature count 31 *****************
******* Condition (False, 1, 61) for feature co

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  402    0.285714  4122.319958
1  485    0.214286  4721.327643
2  459    0.166667  4618.728844
3  476    0.166667  4348.020128
4  447    0.166667  4180.372870

********************** Feature count 43 *****************
******* Condition (False, 1, 61) for feature count 43 *****************
imp_feats_count: 43
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_no


********************** Feature count 54 *****************
******* Condition (False, 1, 61) for feature count 54 *****************
imp_feats_count: 54
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_nonce', 'roll_53_nonce', 'roll_33_nonce', 'roll_8_nonce', 'roll_60_nonce', 'roll_48_nonce', 'roll_0_nonce', 'roll_47', 'roll_12_nonce', 'roll_mean_25_50_nonce', 'roll_18_nonce', 'roll_std', 'roll_15_nonce', 'roll_

...

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  395    0.032258  5033.100576
1  529    0.043011  5003.406383
2  518    0.043011  5296.382092
3  489    0.043011  5439.269619
4  553    0.053763  4771.265068

********************** Feature count 94 *****************
******* Condition (False, 1, 66) for feature count 94 *****************
imp_feats_count: 94
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_no


********************** Feature count 120 *****************
******* Condition (False, 1, 66) for feature count 120 *****************
imp_feats_count: 120
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_nonce', 'roll_53_nonce', 'roll_33_nonce', 'roll_8_nonce', 'roll_60_nonce', 'roll_48_nonce', 'roll_0_nonce', 'roll_47', 'roll_12_nonce', 'roll_mean_25_50_nonce', 'roll_18_nonce', 'roll_std', 'roll_15_nonce', 'ro


********************** Feature count 146 *****************
******* Condition (False, 1, 66) for feature count 146 *****************
imp_feats_count: 146
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_nonce', 'roll_53_nonce', 'roll_33_nonce', 'roll_8_nonce', 'roll_60_nonce', 'roll_48_nonce', 'roll_0_nonce', 'roll_47', 'roll_12_nonce', 'roll_mean_25_50_nonce', 'roll_18_nonce', 'roll_std', 'roll_15_nonce', 'ro

      k  ratio_mean    roll_mean
3   477        0.05  5465.777270
30  552        0.09  5237.189534
44  501        0.11  4745.241087
46  506        0.11  5145.127723

 100 feats success positions
[4, 31, 45, 47]

******101 feats success data *****
      k  ratio_mean    roll_mean
3   477    0.049505  5468.145811
30  552    0.089109  5272.256964
44  501    0.108911  4741.109987
46  506    0.108911  5108.839330

 101 feats success positions
[4, 31, 45, 47]

******102 feats success data *****
      k  ratio_mean    roll_mean
3   477    0.049020  5464.713009
29  552    0.088235  5257.068170
44  501    0.107843  4714.344203
46  506    0.107843  5149.958552

 102 feats success positions
[4, 30, 45, 47]

******103 feats success data *****
      k  ratio_mean    roll_mean
2   477    0.048544  5460.842009
28  552    0.087379  5287.242266
45  506    0.106796  5118.230799
50  501    0.116505  4677.661249

 103 feats success positions
[3, 29, 46, 51]

******104 feats success data *****
      k  rat

imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  \
0                   2           0  roll_10_nonce           False   
1                   3           0  roll_10_nonce           False   
2                   4           0  roll_10_nonce           False   
3                   5           0  roll_10_nonce           False   
4                   6           0  roll_10_nonce           False   
...               ...         ...            ...             ...   
2975              146           4  roll_27_nonce            True   
2976              147           4  roll_27_nonce            True   
2977              148           4  roll_27_nonce            True   
2978              149           4  roll_27_nonce            True   
2979              150           4  roll_27_nonce            True   

      roll_mean_asc  first_match_pos           other_match_pos  
0             False                3  [11, 13, 24, 37, 48, 61]  
1             False                5  [23, 27, 39, 53, 57, 60]  
2             False               14  [24, 32, 38, 47, 57, 59]  
3             False                6  [24, 30, 50, 51, 52, 60]  
4             False                7  [22, 31, 48, 51, 52, 58]  
...             ...              ...                       ...  
2975           True               12              [27, 39, 58]  
2976           True               12              [27, 39, 58]  
2977           True               12              [27, 39, 58]  
2978           True               12              [27, 39, 58]  
2979           True               12              [27, 39, 58]  

[2980 rows x 7 columns]

In [145]:
# match_pos_df.to_csv(f'data/analysis/match_pos_df_hash_{nonce}_{k_bin_size}_hashimp.csv',index=False)
# match_pos_df[match_pos_df['ratio_mean_asc']==False]

In [128]:
%%time
# imp_feats_count_list = [2,5,10,15,20,25,30,35,40,45,50,55,60]
# imp_feats_count_list= [2]+list(range(5,201,5))
# imp_feats_count_list= list(range(2,151))
# imp_feats_count_list= list(range(150,250,10))

# imp_feats_count_list = [2,5]
imp_feats_size = len(imp_feats_count_list)
dictionary_list=[]

top_n = len(all_k)
print(f'\ntop_n:{top_n}')

for ratio_mean_order in [False,True]:
    for roll_mean_order in [False,True]:

        print(f'****************** ACTUAL ratio_mean asc {ratio_mean_order} roll_mean asc {roll_mean_order} *******************')
        sim_cutoff_dfs_actual=None
        cutoff_pos_df_actual,sim_cutoff_dfs_actual,top_mean_actual=create_cutoff_pos_df(test,xgb_models,
                            features_test,df[df.index.isin(all_k)],
                            imp_feats_count_list,test_all_k,is_compute_matches=False,
                           test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs_actual,
                            low_high_record_condns=[(False,1,top_n)],
                            ratio_mean_asc=ratio_mean_order,
                            roll_mean_asc=roll_mean_order,#not(HIGH_ANALYSIS)
                            )

        for feats_idx in range(imp_feats_size):
            cur_top_data = top_mean_actual[feats_idx]
            print(f'\n******{imp_feats_count_list[feats_idx]} feats success data *****')
            mask= cur_top_data['k'].isin(top_k_ele)
            print(cur_top_data[mask])
            cur_positions = list(cur_top_data[mask].index+1)

            dictionary_data = {'imp_feats_count': imp_feats_count_list[feats_idx],
                               'hash_index':-1, 
                               'hash_feat_name': 'ACTUAL', 
                                'ratio_mean_asc':ratio_mean_order,
                                'roll_mean_asc':roll_mean_order,
                                'first_match_pos':cur_positions[0],
                                'other_match_pos':cur_positions[1:]
                  }
            dictionary_list.append(dictionary_data)
            print(f'\n {imp_feats_count_list[feats_idx]} feats success positions')
            print(cur_positions)


match_pos_df_actual = pd.DataFrame.from_dict(dictionary_list)

print()
print('First Match Pos Mean:',match_pos_df_actual.groupby(['ratio_mean_asc','roll_mean_asc'])['first_match_pos'].mean().reset_index())
print()
match_pos_df_actual.head()        



top_n:64
****************** ACTUAL ratio_mean asc False roll_mean asc False *******************
max_good_k=375

********************** Feature count 2 *****************
******* Condition (False, 1, 64) for feature count 2 *****************
imp_feats_count: 2
[['roll_std_50_60_nonce', 'roll_10_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0  550         0.5  1976.122312
1  463         0.5  1946.908271
2    4         0.5  1762.762123
3  494         0.5  1703.893201
4  569         0.5  1576.513353

********************** Feature count 3 *****************
******* Condition (False, 1, 64) for feature count 3 *****************
imp_feats_count: 3
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0  569    0.333333  3856.675569
1  550    0.333333  3829.748208
2  492    0.333333  3776.229119
3   23    0.333333  3091.485380
4    4    0.333333  2998.174748

********************** Feature count 4 *****************
*******


********************** Feature count 29 *****************
******* Condition (False, 1, 64) for feature count 29 *****************
imp_feats_count: 29
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0   63    0.241379  4364.191564
1  462    0.206897  4527.266594
2  459    0.206897  4186.363626
3  415    0.172414  5069.652843
4  494    0.172414  4555.460047

********************** Feature count 30 *****************
******* Condition (False, 1, 64) for feature count 30 **********

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  472    0.178571  4859.052842
1   63    0.178571  4606.026363
2  572    0.160714  4952.185014
3  507    0.160714  4905.779926
4  550    0.160714  4888.879344

********************** Feature count 57 *****************
******* Condition (False, 1, 64) for feature count 57 *****************
imp_feats_count: 57
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_no


********************** Feature count 84 *****************
******* Condition (False, 1, 64) for feature count 84 *****************
imp_feats_count: 84
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_nonce', 'roll_53_nonce', 'roll_33_nonce', 'roll_8_nonce', 'roll_60_nonce', 'roll_48_nonce', 'roll_0_nonce', 'roll_47', 'roll_12_nonce', 'roll_mean_25_50_nonce', 'roll_18_nonce', 'roll_std', 'roll_15_nonce', 'roll_

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  572    0.163636  4821.110547
1  472    0.154545  4535.528709
2  463    0.145455  4749.455696
3   63    0.145455  4706.991060
4   26    0.136364  5024.014053

********************** Feature count 111 *****************
******* Condition (False, 1, 64) for feature count 111 *****************
imp_feats_count: 111
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6

...

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  468    0.021053  5535.891506
1  502    0.042105  5377.352877
2  478    0.052632  4894.411246
3  405    0.063158  4321.132365
4  442    0.063158  4431.641494

********************** Feature count 96 *****************
******* Condition (False, 1, 64) for feature count 96 *****************
imp_feats_count: 96
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6_no

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  468    0.040984  5355.606250
1  433    0.049180  5106.109962
2  502    0.049180  5376.594129
3  405    0.065574  4626.318845
4  570    0.065574  4784.596450

********************** Feature count 123 *****************
******* Condition (False, 1, 64) for feature count 123 *****************
imp_feats_count: 123
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6

--- Top 5 data ---
     k  ratio_mean    roll_mean
0  468    0.036232  5343.999728
1  502    0.043478  5495.235390
2  405    0.065217  4733.607964
3  433    0.065217  5016.343590
4  442    0.072464  4447.765699

********************** Feature count 150 *****************
******* Condition (False, 1, 64) for feature count 150 *****************
imp_feats_count: 150
[['roll_std_50_60_nonce', 'roll_10_nonce', 'roll_37_nonce', 'roll_23_nonce', 'roll_38_nonce', 'roll_mean_25_50', 'roll_mean_1_60', 'roll_std_25_50_nonce', 'roll_27_nonce', 'roll_44_nonce', 'roll_49', 'roll_43_nonce', 'roll_49_nonce', 'roll_22_nonce', 'roll_16_nonce', 'roll_21_nonce', 'roll_std_1_60_nonce', 'roll_13_nonce', 'roll_56_nonce', 'roll_39_nonce', 'roll_58_nonce', 'roll_45_nonce', 'roll_11_nonce', 'roll_55', 'roll_54_nonce', 'roll_mean_50_60_nonce', 'roll_29_nonce', 'roll_40_nonce', 'roll_41_nonce', 'roll_34_nonce', 'roll_27', 'roll_28_nonce', 'roll_30_nonce', 'roll_mean_1_60_nonce', 'roll_35', 'roll_35_nonce', 'roll_6

      k  ratio_mean    roll_mean
0   468    0.018868  5458.235495
19  417    0.075472  5543.375258
24  485    0.084906  5151.147629
38  427    0.103774  4591.097483
40  617    0.103774  4639.438949
43  459    0.103774  4899.615713
47  544    0.103774  5193.458963
53  489    0.122642  4460.477852
61  463    0.150943  4651.472892

 106 feats success positions
[1, 20, 25, 39, 41, 44, 48, 54, 62]

******107 feats success data *****
      k  ratio_mean    roll_mean
0   468    0.018692  5494.485631
19  417    0.074766  5560.278293
23  485    0.084112  5171.445314
36  427    0.102804  4571.591899
39  617    0.102804  4642.836716
42  459    0.102804  4898.423043
44  544    0.102804  5184.454674
52  489    0.121495  4433.211704
61  463    0.149533  4674.141370

 107 feats success positions
[1, 20, 24, 37, 40, 43, 45, 53, 62]

******108 feats success data *****
      k  ratio_mean    roll_mean
0   468    0.018519  5479.175578
17  417    0.074074  5559.266457
23  485    0.083333  5204.765265
33  

imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  roll_mean_asc  \
0                2          -1         ACTUAL           False          False   
1                3          -1         ACTUAL           False          False   
2                4          -1         ACTUAL           False          False   
3                5          -1         ACTUAL           False          False   
4                6          -1         ACTUAL           False          False   

   first_match_pos                   other_match_pos  
0                2  [12, 17, 39, 49, 50, 54, 60, 62]  
1                7  [17, 24, 31, 43, 48, 53, 55, 62]  
2                9  [23, 32, 34, 37, 47, 48, 57, 58]  
3                6  [25, 27, 29, 35, 39, 56, 58, 63]  
4                7  [26, 27, 31, 34, 35, 57, 59, 62]

In [146]:
# match_pos_df_actual.to_csv(f'data/analysis/match_pos_df_actual_{nonce}_{k_bin_size}_hashimp.csv',index=False)

In [56]:
# #2710
# top_k_imp=[[(28, 1.0, 1), (461, 1.0, 1), (495, 1.0, 1)],
#               [(31, 1.0, 1), (451, 1.0, 1), (490, 1.0, 1), (506, 1.0, 1)],
#               [(520, 1.0, 1)],
#               [(13, 1.0, 1), (398, 1.0, 1), (410, 1.0, 1), (425, 1.0, 1), (431, 1.0, 1), (471, 1.0, 1), (481, 1.0, 1), (507, 1.0, 1), (531, 1.0, 1)],
#               [(368, 1.0, 1), (395, 1.0, 1), (440, 1.0, 1), (533, 1.0, 1), (545, 1.0, 1), (573, 1.0, 1), (591, 1.0, 1)]
#                 ]

# all_k_imp  = [[2, 5, 12, 13, 28, 29, 371, 398, 407, 414, 420, 423, 425, 426, 427, 430, 431, 432, 433, 434, 435, 436, 438, 441, 443, 444, 448, 449, 453, 455, 461, 462, 464, 466, 469, 471, 472, 473, 476, 477, 481, 482, 483, 486, 488, 489, 494, 495, 497, 499, 504, 507, 512, 513, 518, 519, 523, 526, 528, 535, 539, 541, 549, 551, 555, 567, 572, 580, 582, 609, 640],
#              [7, 8, 12, 13, 26, 28, 29, 30, 31, 44, 46, 397, 399, 408, 416, 418, 422, 423, 426, 427, 429, 432, 434, 437, 440, 446, 447, 449, 450, 451, 460, 462, 466, 468, 471, 472, 480, 486, 487, 490, 492, 500, 501, 506, 513, 531, 533, 537, 559, 560, 576, 581, 584, 595, 599, 602, 610],
#              [2, 5, 26, 28, 29, 30, 46, 394, 400, 406, 407, 409, 411, 412, 414, 416, 427, 430, 440, 441, 442, 443, 446, 447, 454, 460, 463, 470, 478, 480, 481, 482, 483, 484, 487, 489, 494, 495, 505, 506, 507, 517, 520, 521, 530, 538, 539, 544, 546, 576, 579, 580, 583, 585, 589, 593, 598, 599, 618, 621],
#             [2, 3, 13, 26, 29, 72, 384, 389, 390, 394, 398, 406, 410, 412, 415, 416, 421, 422, 425, 431, 433, 436, 441, 443, 445, 446, 448, 449, 450, 453, 455, 459, 464, 467, 468, 471, 473, 475, 476, 477, 478, 481, 482, 484, 486, 491, 492, 493, 506, 507, 508, 514, 517, 521, 527, 531, 533, 535, 540, 543, 553, 560, 566, 596, 597, 604, 634, 680],
#             [11, 18, 71, 368, 376, 378, 390, 395, 410, 411, 416, 418, 420, 422, 424, 425, 426, 428, 429, 434, 436, 440, 446, 448, 450, 451, 452, 453, 454, 456, 458, 460, 461, 463, 468, 469, 470, 474, 478, 482, 483, 484, 487, 490, 491, 493, 496, 498, 500, 504, 505, 512, 514, 515, 520, 524, 529, 530, 532, 533, 545, 558, 560, 571, 572, 573, 574, 576, 588, 591, 596, 599, 675]
#             ]
# # top_k = [(461, 1.0, 1), (480, 1.0, 1), (503, 1.0, 1), (550, 1.0, 1), (599, 1.0, 1), (603, 1.0, 1)]

# top_k_ele = [461,480,503,550,599,603]
# all_k = [4, 7, 16, 17, 24, 28, 29, 43, 380, 396, 400, 403, 
#          406, 409, 414, 415, 416, 418, 419, 420, 426, 433, 435, 
#          437, 440, 442, 444, 449, 451, 452, 456, 461, 462, 463, 465, 
#          466, 467, 472, 474, 480, 482, 496, 497, 500, 503, 504, 512, 
#          515, 520, 524, 528, 531, 542, 550, 558, 560, 564, 565, 568, 599, 603, 668, 680]
   

In [67]:

# top_k_ele_flat=[]
# for hash_idx in range(5):
# #     top_k_ele_imp[hash_idx] = [x[0] for x in top_k_imp[hash_idx]]
#     for x in top_k_imp[hash_idx]:
#         top_k_ele_flat.append(x[0])
# top_k_ele_flat = list(set(sorted(top_k_ele_flat)))
# print(top_k_ele_flat)  

# all_k_ele_flat=[val for sublist in all_k_imp for val in sublist]
# all_k_ele_flat = list(set(sorted(all_k_ele_flat)))
# print(all_k_ele_flat)  
    
    
# # top_k_ele = sorted([x[0] for x in top_k])
# print('top_k_ele:',top_k_ele)


# diff = set(all_k).difference(set(all_k_ele_flat))
# # diff = set(all_k).difference(set(top_k_ele_flat))
# print(len(all_k),len(diff))
# print(sorted(list(diff)))

# eff_top_k = set(top_k_ele).intersection(diff)
# print(eff_top_k)
# print(f'total success: {len(top_k_ele)} total k:{len(all_k)} ')
# print(f'total eff success: {len(eff_top_k)} total eff: {len(diff)}')

[0, 517, 521, 528, 529, 415, 548, 561, 437, 567, 442, 454, 458, 461, 464, 473, 474, 484, 635, 632, 497, 504, 507, 639]
[0, 1, 512, 513, 514, 515, 517, 519, 8, 521, 522, 523, 524, 525, 14, 526, 527, 528, 529, 530, 531, 532, 533, 537, 538, 27, 28, 539, 540, 543, 546, 547, 548, 549, 550, 551, 552, 553, 554, 559, 48, 560, 561, 563, 52, 564, 55, 567, 568, 572, 573, 574, 576, 577, 578, 579, 580, 582, 586, 587, 589, 591, 593, 598, 599, 601, 604, 605, 606, 611, 613, 616, 617, 619, 622, 626, 630, 632, 633, 635, 638, 639, 132, 650, 652, 662, 672, 675, 676, 677, 691, 351, 356, 361, 365, 366, 367, 368, 369, 374, 379, 380, 381, 384, 390, 393, 396, 398, 399, 401, 403, 404, 409, 410, 412, 413, 414, 415, 416, 417, 419, 420, 422, 424, 425, 426, 427, 429, 430, 432, 433, 434, 435, 436, 437, 438, 439, 440, 441, 442, 443, 444, 445, 446, 447, 448, 449, 450, 451, 452, 454, 455, 456, 457, 458, 459, 460, 461, 462, 463, 464, 466, 467, 469, 470, 471, 472, 473, 474, 475, 476, 477, 478, 479, 480, 481, 482, 483, 48

In [68]:
cur_nonce = 2712

In [69]:
match_pos_df=pd.read_csv(f'data/analysis/match_pos_df_hash_{cur_nonce}_700.csv')
print(len(match_pos_df))
match_pos_df.head()

2980


imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  roll_mean_asc  \
0                2           0  roll_30_nonce           False          False   
1                3           0  roll_30_nonce           False          False   
2                4           0  roll_30_nonce           False          False   
3                5           0  roll_30_nonce           False          False   
4                6           0  roll_30_nonce           False          False   

   first_match_pos               other_match_pos  
0                1  [10, 17, 22, 44, 51, 53, 57]  
1               15  [17, 23, 42, 47, 51, 54, 59]  
2                6  [21, 35, 39, 42, 49, 54, 57]  
3                6  [25, 30, 47, 49, 50, 53, 59]  
4                2  [19, 32, 42, 47, 53, 58, 59]

In [70]:
match_pos_df_actual=pd.read_csv(f'data/analysis/match_pos_df_actual_{cur_nonce}_700.csv')
print(len(match_pos_df_actual))
match_pos_df_actual.head()

596


imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  roll_mean_asc  \
0                2          -1         ACTUAL           False          False   
1                3          -1         ACTUAL           False          False   
2                4          -1         ACTUAL           False          False   
3                5          -1         ACTUAL           False          False   
4                6          -1         ACTUAL           False          False   

   first_match_pos other_match_pos  
0               10              []  
1               14              []  
2               35              []  
3               31              []  
4               44              []

In [71]:
# k_order_df=pd.read_csv(f'data/analysis/k_order_df_hash_{cur_nonce}_700.csv')
# print(len(k_order_df))
# k_order_df_actual=pd.read_csv(f'data/analysis/k_order_df_actual_{cur_nonce}_700.csv')
# print(len(k_order_df_actual))

In [72]:
# all_k_actual =[0, 4, 22, 128, 376, 405, 413, 422, 424, 429, 431, 434, 435, 
#                437, 439, 440, 445, 447, 450, 452, 453, 455, 456, 459, 461, 
#                462, 463, 464, 471, 475, 476, 477, 479, 480, 483, 484, 486, 
#                492, 494, 497, 503, 505, 515, 516, 517, 518, 520, 521, 524, 
#                527, 528, 535, 536, 539, 541, 545, 546, 547, 549, 550, 557, 
#                560, 563, 578, 579, 588, 591, 597, 606, 610, 611, 617, 620, 
#                625, 644, 672, 678]
# top_k_actual =[422, 497, 535, 536, 550, 579]
# print(len(all_k_actual),len(top_k_actual))


In [73]:
# cols = ['hash_idx','k','imp_feats_40','imp_feats_35']
# col_to_sort = 'imp_feats_10'
# mask_temp = (k_order_df_actual['ratio_mean_asc']==0) & (k_order_df_actual['roll_mean_asc']==0) 
# k_order_df_filt_actual = k_order_df_actual[mask_temp]
# k_order_df_filt_actual = k_order_df_filt_actual.sort_values(col_to_sort)
# k_list = k_order_df_filt_actual['k'][:5].to_numpy()
# print(k_list)
# k_order_df_filt_actual[cols].head(5)

In [74]:
# cols = ['hash_idx','k','imp_feats_10','imp_feats_35','imp_feats_40','ratio_mean_asc','roll_mean_asc']
# mask_temp = (k_order_df['ratio_mean_asc']==0) & (k_order_df['roll_mean_asc']==0) \
#             & (k_order_df['k'].isin(k_list)) \
#             & (k_order_df['imp_feats_40']<=100)
# # mask_temp = (k_order_df['k'].isin(k_list))

# k_order_df_filt = k_order_df[mask_temp]
# imp_feats_cols= [col for col in k_order_df_filt.columns if col.startswith('imp_feats')]
# k_order_df_filt['imp_mean']=k_order_df_filt[imp_feats_cols].mean(axis=1)
# # k_order_df_filt[['imp_mean']+cols]
# k_order_df_filt = k_order_df_filt.sort_values(col_to_sort)
# # k_order_df_filt=k_order_df_filt.groupby('k')['imp_mean'].mean().reset_index()
# # k_order_df_filt
# k_order_df_filt[['imp_mean']+cols]
# # rej_k_list = k_order_df_filt['k'].values
# # print(len(rej_k_list))
# # np.sort(rej_k_list)

In [75]:
# set(rej_k_list).intersection(set(top_k_actual))
# eff_all_k = set(all_k_actual).difference(set(rej_k_list))
# eff_top_k = set(top_k_actual).difference(set(rej_k_list))
# print(len(eff_top_k),len(eff_all_k))
# eff_top_k

In [76]:
sel_feats = [2]+list(range(5,61,5))
# sel_feats = None

if isinstance(sel_feats, list):
    print('sel_feats:',sel_feats)
    mask = match_pos_df['imp_feats_count'].isin(sel_feats)
    match_pos_filt_feats = match_pos_df[mask]
else:
    match_pos_filt_feats = match_pos_df
# mask_hash_count = match_pos_filt_feats['hash_index']<=2
# match_pos_filt_feats=   match_pos_filt_feats[mask_hash_count]
match_pos_filt_feats.head()

sel_feats: [2, 5, 10, 15, 20, 25, 30, 35, 40, 45, 50, 55, 60]


imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  roll_mean_asc  \
0                 2           0  roll_30_nonce           False          False   
3                 5           0  roll_30_nonce           False          False   
8                10           0  roll_30_nonce           False          False   
13               15           0  roll_30_nonce           False          False   
18               20           0  roll_30_nonce           False          False   

    first_match_pos               other_match_pos  
0                 1  [10, 17, 22, 44, 51, 53, 57]  
3                 6  [25, 30, 47, 49, 50, 53, 59]  
8                 1  [11, 37, 44, 48, 50, 54, 58]  
13                3  [20, 21, 31, 36, 46, 50, 52]  
18                5  [14, 25, 26, 36, 38, 49, 52]

In [77]:
        
match_summary =match_pos_filt_feats.groupby(['hash_index','ratio_mean_asc','roll_mean_asc'])\
                            .agg(first_match_pos_mean =('first_match_pos','mean'))
                                                                        
print(match_summary.reset_index())
match_top_pos = match_summary['first_match_pos_mean'].groupby('hash_index', group_keys=False).nsmallest(1)
match_top_pos = match_top_pos.reset_index()
print(match_top_pos)


match_freq = match_top_pos.groupby(['ratio_mean_asc','roll_mean_asc']).size().sort_values(ascending=False)
print(match_freq.reset_index())
top_ratio_mean_asc = match_freq.index[0]  
# if len(match_value_counts)==2:
#     ratio_mean_order_equal = match_top_pos['ratio_mean_asc'].value_counts().iloc[0]==match_top_pos['ratio_mean_asc'].value_counts().iloc[1]
#     if ratio_mean_order_equal:
#         print('PROJECT WARNING: Both Ratio mean order ascending and descending are equal')
print(f'\nTop options by frequency : Ratio mean asc={top_ratio_mean_asc[0]}  Roll mean asc={top_ratio_mean_asc[1]}')

    hash_index  ratio_mean_asc  roll_mean_asc  first_match_pos_mean
0            0           False          False              6.538462
1            0           False           True              9.307692
2            0            True          False              4.615385
3            0            True           True              6.000000
4            1           False          False             14.230769
5            1           False           True             18.461538
6            1            True          False              4.307692
7            1            True           True              6.923077
8            2           False          False              7.923077
9            2           False           True              9.384615
10           2            True          False             19.538462
11           2            True           True             20.538462
12           3           False          False              2.692308
13           3           False           True   

In [78]:
match_mean = match_pos_filt_feats.groupby(['ratio_mean_asc','roll_mean_asc'])['first_match_pos'].mean().sort_values(ascending=True)
print(match_mean.reset_index())
top_options = match_mean.index[0]  
print(f'\nTop options by mean : Ratio mean asc={top_options[0]}  Roll mean asc={top_options[1]}')

   ratio_mean_asc  roll_mean_asc  first_match_pos
0           False          False         7.107692
1            True          False         8.676923
2            True           True         9.076923
3           False           True         9.353846

Top options by mean : Ratio mean asc=False  Roll mean asc=False


In [79]:
temp_filt=match_pos_filt_feats.copy()
temp_filt['rank'] = match_pos_filt_feats.groupby('hash_index')['first_match_pos'].rank("min")
mask2=temp_filt['rank']<=5
temp_filt=temp_filt[mask2]
# temp_filt
print(temp_filt['imp_feats_count'].value_counts())

2     6
10    5
5     5
45    4
50    4
55    4
60    4
30    2
35    2
15    2
40    1
Name: imp_feats_count, dtype: int64


In [80]:
temp=match_pos_filt_feats.groupby(['imp_feats_count']).agg(mean =('first_match_pos','mean'),\
                 std =('first_match_pos','std'),
                median = ('first_match_pos','median'),
                minimum = ('first_match_pos','min'),
                maximum = ('first_match_pos','max'),)
temp['mean_rank']=temp['mean'].rank(method='min')
temp['median_rank']=temp['median'].rank(method='min')
temp['min_rank']=temp['minimum'].rank(method='min')
temp['max_rank']=temp['maximum'].rank(method='min')
temp = temp.sort_values(['median','mean','minimum']).reset_index()
temp

imp_feats_count   mean       std  median  minimum  maximum  mean_rank  \
0                 2   4.50  3.252529     3.0        1       11        1.0   
1                10   6.65  6.815424     4.5        1       24        2.0   
2                 5   8.35  9.155240     5.0        1       38        4.0   
3                35   8.10  8.577204     5.5        1       35        3.0   
4                15   8.60  7.358490     5.5        1       25        6.0   
5                40   8.45  7.258208     6.0        2       29        5.0   
6                45   8.80  7.381342     6.0        1       24        7.0   
7                50   9.20  7.557499     6.5        1       24        9.0   
8                30   9.25  9.019715     6.5        1       35       10.0   
9                25   9.65  8.393450     6.5        2       29       11.0   
10               55  10.30  7.834472     8.0        1       25       12.0   
11               20   8.80  4.467426     8.5        3       19        7.0   
12               60  10.55  8.075141     9.0        1       29       13.0   

    median_rank  min_rank  max_rank  
0           1.0       1.0       1.0  
1           2.0       1.0       3.0  
2           3.0       1.0      13.0  
3           4.0       1.0      11.0  
4           4.0       1.0       6.0  
5           6.0      11.0       8.0  
6           6.0       1.0       3.0  
7           8.0       1.0       3.0  
8           8.0       1.0      11.0  
9           8.0      11.0       8.0  
10         11.0       1.0       6.0  
11         12.0      13.0       2.0  
12         13.0       1.0       8.0

In [88]:
# sel_ratio_mean_asc = top_options[0]
# sel_roll_mean_asc = top_options[1]

sel_ratio_mean_asc =   False    
sel_roll_mean_asc =   False

In [89]:
# match_pos_df.groupby('hash_index')
# match_pos_df['rank'] =  match_pos_df['first_match_pos'].rank(method='average',
#                                                              ascending=True)
# mask = (match_pos_df['ratio_mean_asc']==top_ratio_mean_asc)
# pos_top_df= match_pos_df[mask].sort_values(['hash_index','first_match_pos'],ascending=True)\
#             .groupby(['hash_index'])\
#             .head(5)
# print(pos_top_df['imp_feats_count'].value_counts())
# pos_top_df

mask = (match_pos_filt_feats['ratio_mean_asc']==sel_ratio_mean_asc) \
        & (match_pos_filt_feats['roll_mean_asc']==sel_roll_mean_asc)
match_pos_df_filt=match_pos_filt_feats[mask]
match_pos_df_filt['rank'] = match_pos_df_filt.groupby('hash_index')['first_match_pos'].rank("min")
mask2=match_pos_df_filt['rank']<=5
match_pos_df_filt=match_pos_df_filt[mask2]
print(match_pos_df_filt['imp_feats_count'].value_counts())
match_pos_df_filt
# match_pos_df.sort_values(['first_match_pos'],ascending=True)\
#             .groupby(['hash_index','ratio_mean_asc'])\
#             .head(5)\
#             .sort_values(['hash_index','ratio_mean_asc'],ascending=True)
    

2     4
10    3
35    3
5     3
15    2
25    2
20    2
45    2
50    2
60    2
30    1
55    1
Name: imp_feats_count, dtype: int64


imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  \
0                   2           0  roll_30_nonce           False   
8                  10           0  roll_30_nonce           False   
13                 15           0  roll_30_nonce           False   
23                 25           0  roll_30_nonce           False   
28                 30           0  roll_30_nonce           False   
33                 35           0  roll_30_nonce           False   
596                 2           1  roll_50_nonce           False   
599                 5           1  roll_50_nonce           False   
604                10           1  roll_50_nonce           False   
609                15           1  roll_50_nonce           False   
614                20           1  roll_50_nonce           False   
629                35           1  roll_50_nonce           False   
1192                2           2  roll_27_nonce           False   
1195                5           2  roll_27_nonce           False   
1235               45           2  roll_27_nonce           False   
1240               50           2  roll_27_nonce           False   
1250               60           2  roll_27_nonce           False   
1821               35           3        roll_59           False   
1831               45           3        roll_59           False   
1836               50           3        roll_59           False   
1841               55           3        roll_59           False   
1846               60           3        roll_59           False   
2384                2           4  roll_55_nonce           False   
2387                5           4  roll_55_nonce           False   
2392               10           4  roll_55_nonce           False   
2402               20           4  roll_55_nonce           False   
2407               25           4  roll_55_nonce           False   

      roll_mean_asc  first_match_pos                      other_match_pos  \
0             False                1         [10, 17, 22, 44, 51, 53, 57]   
8             False                1         [11, 37, 44, 48, 50, 54, 58]   
13            False                3         [20, 21, 31, 36, 46, 50, 52]   
23            False                2         [17, 25, 26, 39, 43, 45, 55]   
28            False                1         [21, 24, 26, 39, 47, 48, 54]   
33            False                3         [17, 19, 25, 27, 51, 52, 57]   
596           False                5                     [12, 16, 50, 54]   
599           False                6                     [28, 44, 46, 48]   
604           False               10                     [18, 41, 44, 52]   
609           False                5                     [15, 27, 29, 44]   
614           False               10                     [13, 29, 35, 46]   
629           False                9                     [20, 29, 43, 48]   
1192          False                4                         [22, 48, 55]   
1195          False                5                         [24, 62, 64]   
1235          False                2                         [27, 28, 46]   
1240          False                2                         [32, 37, 50]   
1250          False                3                         [36, 37, 52]   
1821          False                1  [7, 10, 15, 22, 40, 42, 45, 47, 55]   
1831          False                1  [5, 11, 12, 28, 34, 43, 44, 47, 58]   
1836          False                1   [2, 9, 13, 17, 35, 36, 39, 49, 58]   
1841          False                1     [3, 6, 8, 9, 14, 40, 43, 51, 58]   
1846          False                1     [2, 5, 6, 8, 16, 38, 44, 49, 52]   
2384          False                2                       [6, 9, 40, 52]   
2387          False                3                     [32, 43, 49, 51]   
2392          False                2                     [13, 24, 33, 51]   
2402          False                3                       [6, 8, 20, 49]   
2407          False   

In [90]:
# match_pos_df.groupby('hash_index')
# match_pos_df['rank'] =  match_pos_df['first_match_pos'].rank(method='average',
#                                                              ascending=True)
mask = (match_pos_filt_feats['ratio_mean_asc']==sel_ratio_mean_asc) \
        & (match_pos_filt_feats['roll_mean_asc']==sel_roll_mean_asc)
# mask = (match_pos_df['ratio_mean_asc']==False)
pos_top_df= match_pos_filt_feats[mask].sort_values(['hash_index','first_match_pos'],ascending=True)\
            .groupby(['imp_feats_count'])\
            .agg(mean =('first_match_pos','mean'),\
                 std =('first_match_pos','std'),
                median = ('first_match_pos','median'),
                minimum = ('first_match_pos','min'),
                maximum = ('first_match_pos','max'),)
#             .sort_values('imp_feats_count')
# print(pos_top_df['imp_feats_count'].value_counts())
pos_mean_summary = pos_top_df.sort_values(['mean','minimum','maximum'],ascending=[True,True,True]).reset_index()
pos_mean_summary['mean_rank']=pos_mean_summary['mean'].rank(method='min')
pos_mean_summary['median_rank']=pos_mean_summary['median'].rank(method='min')
pos_mean_summary['min_rank']=pos_mean_summary['minimum'].rank(method='min')
pos_mean_summary['max_rank']=pos_mean_summary['maximum'].rank(method='min')
pos_mean_summary
# match_pos_df.sort_values(['first_match_pos'],ascending=True)\
#             .groupby(['hash_index','ratio_mean_asc'])\
#             .head(5)\
#             .sort_values(['hash_index','ratio_mean_asc'],ascending=True)
    

imp_feats_count  mean        std  median  minimum  maximum  mean_rank  \
0                 2   3.0   1.581139     3.0        1        5        1.0   
1                 5   4.4   1.816590     5.0        2        6        2.0   
2                35   5.4   3.911521     4.0        1       10        3.0   
3                20   6.0   2.645751     5.0        3       10        4.0   
4                15   6.0   4.527693     4.0        3       14        4.0   
5                30   6.4   4.098780     5.0        1       11        6.0   
6                25   6.6   6.024948     5.0        2       17        7.0   
7                40   7.2   4.658326     7.0        2       14        8.0   
8                10   8.2   9.497368     4.0        1       24        9.0   
9                45   8.4   8.264381     6.0        1       21       10.0   
10               50   9.6   9.762172     6.0        1       24       11.0   
11               55  10.2   9.338094     7.0        1       25       12.0   
12               60  11.0  11.113055     7.0        1       28       13.0   

    median_rank  min_rank  max_rank  
0           1.0       1.0       1.0  
1           5.0       9.0       2.0  
2           2.0       1.0       3.0  
3           5.0      12.0       3.0  
4           2.0      12.0       6.0  
5           5.0       1.0       5.0  
6           5.0       9.0       8.0  
7          11.0       9.0       6.0  
8           2.0       1.0      10.0  
9           9.0       1.0       9.0  
10          9.0       1.0      10.0  
11         11.0       1.0      12.0  
12         11.0       1.0      13.0

In [91]:
# pos_mean_summary[pos_mean_summary['imp_feats_count'].isin([17,22,23,24,25])]

In [92]:
if isinstance(sel_feats, list):
    print('sel_feats:',sel_feats)
    mask = match_pos_df_actual['imp_feats_count'].isin(sel_feats)
    match_pos_actual_filt_feats = match_pos_df_actual[mask]
else:
    match_pos_actual_filt_feats = match_pos_df_actual
    
# match_pos_actual_filt_feats.head()

sel_feats: [2, 5, 10, 15, 20, 25, 30, 35, 40, 45, 50, 55, 60]


In [93]:
mask = (match_pos_actual_filt_feats['ratio_mean_asc']==sel_ratio_mean_asc) \
        & (match_pos_actual_filt_feats['roll_mean_asc']==sel_roll_mean_asc)
match_pos_actual_filt=match_pos_actual_filt_feats[mask]
match_pos_actual_filt.sort_values('first_match_pos',ascending=True)

imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  roll_mean_asc  \
48               50          -1         ACTUAL           False          False   
43               45          -1         ACTUAL           False          False   
53               55          -1         ACTUAL           False          False   
0                 2          -1         ACTUAL           False          False   
58               60          -1         ACTUAL           False          False   
28               30          -1         ACTUAL           False          False   
33               35          -1         ACTUAL           False          False   
38               40          -1         ACTUAL           False          False   
3                 5          -1         ACTUAL           False          False   
13               15          -1         ACTUAL           False          False   
23               25          -1         ACTUAL           False          False   
18               20          -1         ACTUAL           False          False   
8                10          -1         ACTUAL           False          False   

    first_match_pos other_match_pos  
48                5              []  
43                7              []  
53                7              []  
0                10              []  
58               12              []  
28               17              []  
33               22              []  
38               29              []  
3                31              []  
13               33              []  
23               35              []  
18               41              []  
8                54              []

In [94]:
match_pos_actual_filt

imp_feats_count  hash_index hash_feat_name  ratio_mean_asc  roll_mean_asc  \
0                 2          -1         ACTUAL           False          False   
3                 5          -1         ACTUAL           False          False   
8                10          -1         ACTUAL           False          False   
13               15          -1         ACTUAL           False          False   
18               20          -1         ACTUAL           False          False   
23               25          -1         ACTUAL           False          False   
28               30          -1         ACTUAL           False          False   
33               35          -1         ACTUAL           False          False   
38               40          -1         ACTUAL           False          False   
43               45          -1         ACTUAL           False          False   
48               50          -1         ACTUAL           False          False   
53               55          -1         ACTUAL           False          False   
58               60          -1         ACTUAL           False          False   

    first_match_pos other_match_pos  
0                10              []  
3                31              []  
8                54              []  
13               33              []  
18               41              []  
23               35              []  
28               17              []  
33               22              []  
38               29              []  
43                7              []  
48                5              []  
53                7              []  
58               12              []

In [95]:
len(match_pos_df_actual)
print('First Match Pos Mean:',match_pos_actual_filt_feats.groupby(['ratio_mean_asc','roll_mean_asc'])['first_match_pos'].mean().reset_index())

First Match Pos Mean:    ratio_mean_asc  roll_mean_asc  first_match_pos
0           False          False         5.615385
1           False           True         5.076923
2            True          False        11.538462
3            True           True        13.615385


In [164]:
%%time
# imp_feats_count_list = [45]
imp_feats_count_list = [2,5,10,15,20,25,30,35,40,45,50,55,60]
# imp_feats_count_list= [2]+list(range(5,201,5))
# imp_feats_count_list= list(range(2,151))

sim_cutoff_dfs_actual=None
top_n = len(all_k)
cutoff_pos_df_actual,sim_cutoff_dfs_actual,top_mean_actual=create_cutoff_pos_df(test,xgb_models,
                    features_test,df[df.index.isin(all_k)],
                    imp_feats_count_list,test_all_k,is_compute_matches=False,
                   test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs_actual,
                    low_high_record_condns=[(False,1,top_n)],
                    ratio_mean_asc=sel_ratio_mean_asc,
                    roll_mean_asc=sel_roll_mean_asc,
                    top_k_ele=top_k_ele)
cutoff_pos_df_actual

max_good_k=375

********************** Feature count 2 *****************
******* Condition (False, 1, 64) for feature count 2 *****************
imp_feats_count: 2
[['roll_std_50_60_nonce', 'roll_10_nonce']]
--- Top 5 data ---
     k  ratio_mean    roll_mean
0  550         0.5  1976.122312
1  463         0.5  1946.908271
2    4         0.5  1762.762123
3  494         0.5  1703.893201
4  569         0.5  1576.513353

******success data *****
      k  ratio_mean    roll_mean
1   463         0.5  1946.908271
11  544         0.0  6450.857947
16  489         0.0  5927.470682
38  459         0.0  4142.261144
48  427         0.0  3499.548136
49  468         0.0  3360.980846
53  417         0.0  2964.970388
59  485         0.0  2572.114723
61  617         0.0  2232.471331

******success positions *****
[2, 12, 17, 39, 49, 50, 54, 60, 62]

********************** Feature count 5 *****************
******* Condition (False, 1, 64) for feature count 5 *****************
imp_feats_count: 5
[['roll_std

imp_feats_count  condn_max  condn_val  k_top_1  k_top_2  k_top_3  k_top_4  \
0                 2      False          1      550      463        4      494   
1                 5      False          1      492      415      550        4   
2                10      False          1      415      492      462      417   
3                15      False          1      462      415       63       30   
4                20      False          1      462       63      463       30   
5                25      False          1       63      462      463      415   
6                30      False          1       63      462      459      415   
7                35      False          1       63      459      415      472   
8                40      False          1      472       63      459      494   
9                45      False          1      472      459       63      462   
10               50      False          1       63      472      507      550   
11               55      False          1       63      472      415      507   
12               60      False          1      472      550      572       63   

    k_top_5  mean_top_1  mean_top_2  mean_top_3  mean_top_4  mean_top_5  \
0       569    0.500000    0.500000    0.500000    0.500000    0.500000   
1       503    0.400000    0.400000    0.200000    0.200000    0.200000   
2       550    0.300000    0.200000    0.200000    0.200000    0.100000   
3       417    0.333333    0.200000    0.200000    0.200000    0.133333   
4       415    0.300000    0.300000    0.250000    0.200000    0.150000   
5       494    0.280000    0.240000    0.200000    0.160000    0.160000   
6       429    0.233333    0.200000    0.200000    0.166667    0.166667   
7       462    0.200000    0.200000    0.171429    0.171429    0.171429   
8       415    0.200000    0.175000    0.175000    0.175000    0.150000   
9       415    0.177778    0.177778    0.177778    0.155556    0.155556   
10      459    0.180000    0.160000    0.160000    0.160000    0.160000   
11      572    0.181818    0.163636    0.163636    0.163636    0.163636   
12      507    0.183333    0.166667    0.166667    0.166667    0.150000   

    match_pos_1  match_total_top_5  match_total_top_10  match_ks_top_5  
0           NaN                NaN                 NaN             NaN  
1           NaN                NaN                 NaN             NaN  
2           NaN                NaN                 NaN             NaN  
3           NaN                NaN                 NaN             NaN  
4           NaN                NaN                 NaN             NaN  
5           NaN                NaN                 NaN             NaN  
6           NaN                NaN                 NaN             NaN  
7           NaN                NaN                 NaN             NaN  
8           NaN                NaN                 NaN             NaN  
9           NaN                NaN                 NaN             NaN  
10          NaN                NaN                 NaN             NaN  
11          NaN                NaN                 NaN             NaN  
12          NaN                NaN                 NaN             NaN

In [52]:
%%time
k_list = top_mean_actual[1][:5]['k'].values
print(k_list)
# test_sel=test_all_k[test_all_k['k'].isin(k_list)]
# [23, 390, 421, 453, 454, 471, 495, 510, 512]
test_sel=test_all_k[test_all_k['k'].isin(k_list)]
test_sel[['k','roll_actual','client_seed','roll_0','roll_1']]

NameError: name 'top_mean_actual' is not defined

In [53]:
# pos_top_imp_feats = list(pos_top_df['imp_feats_count'].value_counts().index)
# imp_feats_count_arr = np.array(imp_feats_count_list)
# # itemindex = np.where(imp_feats_count_arr in pos_top_imp_feats)
# print(pos_top_imp_feats)
# itemindex= np.searchsorted(imp_feats_count_arr, pos_top_imp_feats)
# itemindex

In [54]:
# sel_imp_feats_top=[]
# for i in itemindex:
#     sel_imp_feats_top.extend(top_mean_actual[i][:5]['k'].values)
# sel_imp_feats_top=np.array(sel_imp_feats_top)
# np.array(np.unique(sel_imp_feats_top, return_counts=True)).T

In [55]:
# %%time
# # imp_feats_count_list = [2,5,10,15,20,25,30,40]
# sim_cutoff_dfs_actual=None
# cutoff_pos_df_actual,sim_cutoff_dfs_actual,test_probs=create_cutoff_pos_df(test,xgb_models,
#                     features_test,df[df.index.isin(trans_k)],
#                     imp_feats_count_list,is_compute_matches=False,
#                    test_ratio_limit=0.12,sim_cutoff_dfs=sim_cutoff_dfs_actual,
#                     low_high_record_condns=[(False,2,20)])
# cutoff_pos_df_actual

In [56]:
# # k_sel,test_sel,cutoff_pos_best =get_test_sel_cutoff_pos(test_probs,cutoff_pos_df_hash,cutoff_pos_df_actual)
# # imp_feats_count_list = [2,5,10,15,20,25]

# k_sel,test_sel,top_mean_best =get_test_sel_cutoff_pos(test_probs,xgb_models,features_test,
#                                                       df,
#                             cutoff_pos_df_hash,
#                             is_min_total=False,total_cri=2,top_n=10,
#                             sim_cutoff_dfs=sim_cutoff_dfs_actual,
#                             imp_feats_count_list=imp_feats_count_list)
# print(f'{k_sel=}')
# print('cutoff best')
# print(top_mean_best)
# print(' ** selected test **')
# test_sel[['k','client_seed','probs']]

In [57]:
%%time
k_list = top_mean_actual[37][:5]['k'].values
test_sel=test_all_k[test_all_k['k'].isin(k_list)]
test_sel

NameError: name 'top_mean_actual' is not defined

In [58]:
%%time
test_sel=None
#array([ 10, 536, 371, 333, 518])
k_list = top_mean_actual[37][:5]['k'].values
print(k_list)
for k_sel in k_list:
    row = df.iloc[k_sel]
#     print(row)
    mask = (test['probs']>=row['cutoff']) & (test['probs']<=row['cutoff_2'])
    cur_test_sel = test[mask]
    cur_test_sel['k']=k_sel
    if test_sel is None:
        test_sel = cur_test_sel
    else:
        test_sel = pd.concat([test_sel,cur_test_sel],axis=0)
    print('Test Size:',len(test_sel))
test_sel[['k','roll_actual','client_seed','roll_0','roll_1']]

NameError: name 'top_mean_actual' is not defined

In [59]:
test_sel

END

In [60]:
imp_feats = [col for col in imp_df['feature'].values if (col.startswith('roll_'))][:10] 
test_sel[['k']+imp_feats]

NameError: name 'imp_df' is not defined

In [61]:
sim_hash_group[sim_hash_group['k']==24]

NameError: name 'sim_hash_group' is not defined

In [62]:
sim_cutoff_df[sim_cutoff_df['k']==24]

NameError: name 'sim_cutoff_df' is not defined

In [63]:
def compute_total(data,cutoffs,cols):
    mask = None
    for cutoff,col in zip(cutoffs,cols):
        cur_mask =(data[col]>=cutoff) 
        if mask is None:
            mask = cur_mask
        else:
            mask = mask & cur_mask
    data_filt = data[mask]
    total = len(data_filt)
    return total,data_filt

In [64]:
cols=['roll_20_nonce','roll_14_nonce','roll_3_nonce','roll_16_nonce','roll_11_nonce']
cols=['roll_43_nonce','roll_56_nonce','roll_31_nonce','roll_20_nonce','roll_45_nonce']
cols=['roll_31_nonce','roll_52_nonce','roll_15_nonce','roll_45_nonce','roll_2_nonce']
cols=['roll_31_nonce','roll_52_nonce']
cols=['roll_52_nonce','roll_31_nonce','roll_24_nonce','roll_49_nonce','roll_41_nonce']
cols=['roll_mean_25_50_nonce','roll_52_nonce','roll_31_nonce']
cols=['roll_52_nonce','roll_31_nonce']
cols=['roll_46_nonce','roll_25_nonce']
cols=['roll_42_nonce','roll_37_nonce']

# cols=['roll_20_nonce','roll_15_nonce','roll_13_nonce','roll_12_nonce','roll_18_nonce']
# cols=['roll_20_nonce','roll_15_nonce','roll_13_nonce']
# cols=['roll_6_nonce','roll_11_nonce','roll_12_nonce','roll_10_nonce',]




In [65]:
def get_cutoff(data,data_hash,col,quantile):
    mask=create_target_mask(data_hash)
#     cutoff = data[col].mean()-data_hash[col].mean()+data_hash[mask][col].mean()
#     cutoff = data_hash[mask][col].quantile(0.5)
    cutoff = data[col].mean()-data_hash[col].mean()+data_hash[mask][col].quantile(quantile)
    return cutoff



best_ratio =0
best_success = 0
best_total = 0
best_cutoffs = []
best_quantile = 0
best_actual = test_filt
# for quantile in np.linspace(0.01,0.95,50):
for quantile in np.linspace(0.01,0.95,50):
    cutoffs=[]
    for col in cols:
        #use entire hash to determine cutoff
        cutoff = get_cutoff(test,test_hash,col,quantile)
        cutoffs.append(cutoff)
    
#     print(cutoffs)
    total,filt_inter = compute_total(test_filt_hash,cutoffs,cols)
    mask2=create_target_mask(filt_inter)
#     mask2 = (filt_inter['roll_actual']>=9000)
    success = len(filt_inter[mask2])
    
    total_actual,filt_inter_actual = compute_total(test_filt,cutoffs,cols)
    mask2=create_target_mask(filt_inter_actual)

#     mask2 = (filt_inter_actual['roll_actual']>=9000)
    
    if total_actual==0:
        success_actual=0
        ratio_actual=0
    else:
        success_actual = len(filt_inter_actual[mask2])
        ratio_actual = success_actual / total_actual
    print('\nquantile:',quantile)
    print('Actuals:',ratio_actual,success_actual,total_actual)
    
    if total==0:
        ratio=0
    else:
        ratio = success / total
    print('Hash:',ratio,success,total)
#     print(quantile,cutoffs)
    print(total,total_actual)
#     print(total,success)
    if (total==0) or (success==0) : #or (total_actual<1):
        break

#     print(ratio,success,total)
    if ratio >= best_ratio:
        best_ratio = ratio
        best_success = success
        best_total = total
        best_cutoffs = cutoffs
        best_quantile = quantile
        best_actual = filt_inter_actual
print(best_quantile)        
print(best_ratio,best_success,best_total)        
print(best_cutoffs)
# print(test_filt[mask]['roll_actual'].describe())

NameError: name 'test_filt' is not defined

In [66]:
mask2=create_target_mask(best_actual)
success = len(best_actual[mask2])
total = len(best_actual)
ratio = success / total
print(ratio,success,total)

NameError: name 'create_target_mask' is not defined

In [67]:
test_sel = best_actual.copy()

NameError: name 'best_actual' is not defined

In [68]:


def get_actual_based_data(data,data_hash,data_filt,cols,total_cutoff=3):

    best_filt_inter = data
    best_total= 0
    best_quantile = 0
    for quantile in np.linspace(0.01,0.95,50):
        cutoffs=[]
        for col in cols:
            cutoff = get_cutoff(data,data_hash,col,quantile)
        #     cutoff = get_cutoff(test,test_hash,col)
            cutoffs.append(cutoff)
#         print(quantile,cutoffs)

        total,filt_inter=compute_total(data_filt,cutoffs,cols)
        if total<total_cutoff:
            break
        best_filt_inter = filt_inter
        best_total = total
        best_quantile = quantile
        
    return best_filt_inter,best_total,best_quantile

In [69]:
for cutoff in range(0,11):

    best_filt_inter,best_total,best_quantile=get_actual_based_data(test,test_hash,test_filt,cols,
                                                                        total_cutoff=cutoff)
#     print('quantile:',best_quantile)
    mask2=create_target_mask(best_filt_inter)
    # mask2 = (best_filt_inter['roll_actual']>=9000)
    success = len(best_filt_inter[mask2])
    if best_total==0:
        ratio=0
        success=0
    else:
        success = len(best_filt_inter[mask2])
        ratio = success / best_total
    print(cutoff, ratio,success,best_total)
    # print(test_filt[mask]['roll_actual'].describe())

NameError: name 'test' is not defined

In [ ]:
test_sel =best_filt_inter.copy()

In [70]:
best_filt_inter,best_total,best_quantile=get_actual_based_data(test_filt,test_filt_hash,test_filt,cols,
                                                              total_cutoff=4)
print('quantile:',best_quantile)
mask2=create_target_mask(best_filt_inter)
# mask2 = (best_filt_inter['roll_actual']>=9000)
success = len(best_filt_inter[mask2])
if best_total==0:
    ratio=0
    success=0
else:
    success = len(best_filt_inter[mask2])
    ratio = success / best_total
print(ratio,success,best_total)
# print(test_filt[mask]['roll_actual'].describe())

NameError: name 'test_filt' is not defined

In [ ]:
# mask_actual = (test_probs['probs']>=row['cutoff']) & (test_probs['probs']<=row['cutoff_2'])
# idx= test_probs[mask_actual].index
# mask_hash = test_hash_probs.index.isin(idx)
# test_filt_hash_pos = test_hash_probs.loc[mask_hash]

mask_hash = (test_hash_probs['probs']>=row['cutoff']) & (test_hash_probs['probs']<=row['cutoff_2'])
idx= test_hash_probs[mask_hash].index
mask_actual = test_probs.index.isin(idx)
test_filt_pos = test_probs.loc[mask_actual]

best_filt_inter,best_total,best_quantile=get_actual_based_data(test,test_hash,
                                                               test_filt_pos,cols,
                                                              total_cutoff=37)
print('quantile:',best_quantile)
mask2=create_target_mask(best_filt_inter)
# mask2 = (best_filt_inter['roll_actual']>=9000)
if best_total==0:
    ratio=0
    success=0
else:
    success = len(best_filt_inter[mask2])
    ratio = success / best_total
print(ratio,success,best_total)
# print(test_filt[mask]['roll_actual'].describe())

In [71]:
best_filt_inter

NameError: name 'best_filt_inter' is not defined

In [72]:
test_sel=best_filt_inter.copy()

NameError: name 'best_filt_inter' is not defined

In [73]:
# analysis_df_copy  = analysis_df.copy()

In [74]:
def report_exceptional_teratio(analysis_df,digitlist,
                     ratio_cutoff,count_cutoff_min,count_cutoff_max,
                     pattern,bHighCheck,
                    zerocolcutoffs,is_ratio_cri_lessthan=False,
                               is_aftval_opp=False,is_aftval_sum=False):
    mask1 = analysis_df['digit'].isin(digitlist)
    if is_ratio_cri_lessthan:
        mask2= (analysis_df['tr_ratio']<ratio_cutoff) 
        if is_aftval_opp:
            mask2= mask2 & ((analysis_df['aft_all']>=ratio_cutoff) | (analysis_df['aft_1']>=ratio_cutoff) | (analysis_df['aft_2']>=ratio_cutoff)) 
    else:
        mask2=  (analysis_df['tr_ratio']>=ratio_cutoff) 
        if is_aftval_opp:
            mask2= mask2 & ((analysis_df['aft_all']<ratio_cutoff) | (analysis_df['aft_1']<ratio_cutoff) | (analysis_df['aft_2']<ratio_cutoff)) \
    
        
    mask= mask1 & mask2 \
             & ((analysis_df['aft_all']!=0) & (analysis_df['aft_1']!=0) & (analysis_df['aft_2']!=0)) \
                & (analysis_df['te_total']>=count_cutoff_min) \
                & (analysis_df['te_total']<=count_cutoff_max) \
                & (analysis_df['pattern_99']==pattern) \
                & (analysis_df['target_high']==bHighCheck) \
                & (analysis_df['zero_col_cutoff'].isin(zerocolcutoffs))
        
    if is_aftval_sum:
        mask= mask & ((analysis_df['aft_all']+analysis_df['aft_1']+analysis_df['aft_2'])>=36) \

    filtered = analysis_df[mask]
    
    records  = len(filtered)
    cols = ['tr_ratio','tr_total','te_total']
    
    return filtered

##### Production Code

In [75]:
# def get_random_client_seed(test):
#     size = len(test)
#     test = test.reset_index(drop=True).sample(n=size).reset_index(drop=True)
#     rand_pos = random.randint(0,size-1)
#     print(f'rand_pos:{rand_pos}')
#     return test.iloc[rand_pos]['client_seed'],test

def get_random_client_seed(test):
    size = len(test)
    final_test= test.sample(n=size)
    rand_pos=random.randint(0,size-1)
    sample=final_test.reset_index(drop=True).loc[rand_pos]
#     rand_pos = sample.index[0]
    print(f'rand_pos:{rand_pos}')
    return sample['client_seed'],final_test

In [76]:
client_seed,final_test = get_random_client_seed(test_sel)
print('Client Seed Selected')
print(client_seed)
# final_test.to_csv(f'data/analysis/final_test_{nonce}.csv')
# final_test.head()

TypeError: object of type 'NoneType' has no len()

In [77]:
final_test

NameError: name 'final_test' is not defined

In [78]:
# final_test.reset_index()[final_test.reset_index()['index']==6826]

After Actual SEED is known

In [79]:
actual_seed="10becea2d59d28973731f248e5e05678c26a79733b5e6ff218f49fdd72e0ff42"
# actual_seed=cur_hash_list[4]
# print(f'{actual_seed=}')

In [80]:
# Vectorize the function
vectorized_calculate_roll = np.vectorize(calculate_roll)

# Compute the roll values for the input arrays
roll_array = vectorized_calculate_roll(actual_seed,
                                       final_test['client_seed'],
                                       nonce)
final_test['roll_actual_dummy']=final_test['roll_actual'].copy()
final_test['roll_actual']=roll_array
# final_test.to_csv(f'data/analysis/final_test_{nonce}.csv')

NameError: name 'calculate_roll' is not defined

In [81]:
final_test

NameError: name 'final_test' is not defined

In [82]:
final_test.to_csv(f'data/final_test_{nonce}_{file_pattern_str}_pattern.csv')

NameError: name 'final_test' is not defined

In [ ]:
LOW_TARGET

In [83]:
mask = create_target_mask(final_test)
success_pos = final_test[mask].index

if HIGH_ANALYSIS:
    success_pos = final_test[final_test['roll_actual']>=HIGH_TARGET].index
else:
    success_pos = final_test[final_test['roll_actual']<LOW_TARGET].index
print(len(success_pos))
print(f'success_pos:{success_pos}')

# target = set([17, 19, 34, 35, 44, 47])
# matched  = set(list(success_pos)).intersection(target)
# print(matched)

# print(len(matched)/len(success_pos))

NameError: name 'create_target_mask' is not defined

In [ ]:
test_sel.head()

In [84]:
final_test

NameError: name 'final_test' is not defined

In [85]:
# Vectorize the function
vectorized_calculate_roll = np.vectorize(calculate_roll)

# Compute the roll values for the input arrays
roll_array = vectorized_calculate_roll(actual_seed,
                                       results_df_test['client_seed'],
                                       nonce)

results_df_test['roll_actual']=roll_array
test_manual = generate_test_features(results_df_test)
test = generate_features_full(results_df_test,False,feature_chain_length)


analysis_df,test = gen_analysis(nonce,train_manual,test_manual,test,xgb_models,tr_last_cutoffs,val_cutoffs,
                multi_models=True,file_suffix="")
analysis_df.head()

NameError: name 'calculate_roll' is not defined

#### END

Finalize Training

In [86]:
tr_index

NameError: name 'tr_index' is not defined

In [87]:
train.index

NameError: name 'train' is not defined

In [88]:
# tr_index = train[30 * train_client_size:(30 + 5) * train_client_size].index
tr_index = train[train_client_size:].index
train_ignored = train[0:30*train_client_size]
# tr_index = list(tr_index) + list(train_ignored[train_ignored['target']==1].index)
print(len(tr_index))
xgb_model_final = xgb.XGBClassifier(**params)

X_tr,y_tr = X.iloc[tr_index],y.iloc[tr_index]
oversample = RandomOverSampler(sampling_strategy='minority',random_state=123)
# fit and apply the transform
X_tr, y_tr = oversample.fit_resample(X_tr, y_tr)
print(pd.Series(y_tr).value_counts())
xgb_model_final.fit(X_tr,y_tr)

NameError: name 'train' is not defined

In [ ]:
len(X_tr)

In [89]:
test_probs = xgb_model_final.predict_proba(test)[:,1]

test_labels = convert_probtolabels(test_probs)
subm=pd.DataFrame()
subm['client_seed']= results_df_test['client_seed']
subm['preds'] = test_labels
subm['prob'] = test_probs
score = accuracy_score(y_test,test_labels)
print(f'test score:{score}')

NameError: name 'xgb_model_final' is not defined

In [ ]:
mask = (subm['prob']<0.52) & (subm['preds']==1)
print(len(subm[mask]))
score = accuracy_score(y_test[mask],test_labels[mask])
print(f'test score:{score}')